In [1]:
import pandas as pd
import numpy as np
from matplotlib import pyplot as plt
import seaborn as sns
import statsmodels.api as sm
from sklearn.model_selection import train_test_split, GridSearchCV, cross_val_score
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler, OneHotEncoder, FunctionTransformer, OrdinalEncoder
from sklearn.impute import SimpleImputer
from sklearn.compose import ColumnTransformer
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier, GradientBoostingClassifier, StackingClassifier
from sklearn.metrics import plot_confusion_matrix, recall_score,\
    accuracy_score, precision_score, f1_score
%matplotlib inline
from imblearn.over_sampling import SMOTE
from imblearn.pipeline import Pipeline as ImPipeline
from sklearn.dummy import DummyClassifier
import xgboost
import pickle
import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)

### Loading in Data

In [2]:
allstar_df = pd.read_csv("../data/AllstarFull.csv")

In [3]:
awards1_df = pd.read_csv("../data/AwardsPlayers.csv")

In [4]:
awards2_df = pd.read_csv("../data/AwardsSharePlayers.csv")

In [5]:
batting_df = pd.read_csv("../data/Batting.csv")

In [6]:
people_df = pd.read_csv("../data/People.csv")

In [7]:
salaries_df = pd.read_csv("../data/Salaries.csv")

In [8]:
salary2_df = pd.read_csv("../data/Salary2.csv", encoding='iso-8859-1')

Found the salary2_df data at [Cot's Baseball Contracts](https://legacy.baseballprospectus.com/compensation/cots/). This data included salary data from 2000-2021, and helped me fill in 1600 values in the original salary column that were null.

In [9]:
salary3_df = pd.read_csv("../data/salary_history.csv", encoding='iso-8859-1')

Found the salary3_df data at [The Baseball Cube](https://www.thebaseballcube.com/content/store).  This data included salary data from 1985-2022.  I purchased this data set for $20.

In [10]:
teams_df = pd.read_csv("../data/Teams.csv")

### Data Exploration

#### Cleaning batting_df

In [11]:
batting_df.tail(10)

playerID  yearID  stint teamID lgID    G   AB   R   H  2B  ...   RBI  \
110485  zavalse01    2021      1    CHA   AL   37   93  15  17   3  ...  15.0   
110486  zerpaan01    2021      1    KCA   AL    1    0   0   0   0  ...   0.0   
110487  zeuchtj01    2021      1    TOR   AL    5    0   0   0   0  ...   0.0   
110488  zimmebr01    2021      1    CLE   AL   99  299  44  68   9  ...  35.0   
110489  zimmebr02    2021      1    BAL   AL   14    4   0   0   0  ...   0.0   
110490  zimmejo02    2021      1    MIL   NL    2    1   0   0   0  ...   0.0   
110491  zimmeky01    2021      1    KCA   AL   52    0   0   0   0  ...   0.0   
110492  zimmery01    2021      1    WAS   NL  110  255  27  62  16  ...  46.0   
110493  zuberty01    2021      1    KCA   AL   31    1   0   0   0  ...   0.0   
110494  zuninmi01    2021      1    TBA   AL  109  333  64  72  11  ...  62.0   

          SB   CS  BB     SO  IBB   HBP   SH   SF  GIDP  
110485   0.0  0.0   6   41.0  0.0   1.0  4.0  0.0   1.0  
110486   0.0  0.0   0    0.0  0.0   0.0  0.0  0.0   0.0  
110487   0.0  0.0   0    0.0  0.0   0.0  0.0  0.0   0.0  
110488  15.0  3.0  30  122.0  0.0  15.0  0.0  4.0   3.0  
110489   0.0  0.0   0    3.0  0.0   0.0  0.0  0.0   0.0  
110490   0.0  0.0   0    1.0  0.0   0.0  0.0  0.0   0.0  
110491   0.0  0.0   0    0.0  0.0   0.0  0.0  0.0   0.0  
110492   0.0  0.0  16   77.0  0.0   0.0  0.0  2.0   9.0  
110493   0.0  0.0   0    1.0  0.0   0.0  0.0  0.0   0.0  
110494   0.0  0.0  34  132.0  0.0   7.0  0.0  1.0   7.0  

[10 rows x 22 columns]

In [12]:
batting_df.columns

Index(['playerID', 'yearID', 'stint', 'teamID', 'lgID', 'G', 'AB', 'R', 'H',
       '2B', '3B', 'HR', 'RBI', 'SB', 'CS', 'BB', 'SO', 'IBB', 'HBP', 'SH',
       'SF', 'GIDP'],
      dtype='object')

Need to add columns for Batting Average (AVG), On Base Percentage (OBP), Slugging Percentage (SLG), On Base + Slugging (OPS), Strikeout percentage, and walk percentage

Can drop H, 2B, 3B, BB, SO, after creating the new columns.

Also want to drop HBP, SH, SF, GIDP, CS, IBB

In [13]:
#Creating a Plate Appearances column
batting_df['PA'] = (batting_df['AB'] + batting_df['HBP'] + batting_df['BB'] + batting_df['SF'] + batting_df['SH'] + batting_df['IBB'])

In [14]:
#Creating a Batting Average column
batting_df['AVG'] = batting_df['H'] / batting_df['AB']

In [15]:
#Creating an On Base Percentage column
batting_df['OBP'] = (batting_df['H'] + batting_df['BB'] + batting_df ['HBP']) / batting_df['PA']

In [16]:
#Creating a Slugging Percentage column
batting_df['SLG'] = ((batting_df['H'] - batting_df['2B'] - batting_df['3B'] - batting_df['HR']) + (2 * batting_df['2B']) + (3 * batting_df['3B'] + (4 * batting_df['HR']))) / batting_df['AB']

In [17]:
#Creating an On Base Plus Slugging Percentage column
batting_df['OPS'] = batting_df['OBP'] + batting_df['SLG']

In [18]:
#Creating a Strikeout Percentage column
batting_df['K%'] = 100 * (batting_df['SO'] / batting_df['PA'])

In [19]:
#Creating a Walk Percentage column
batting_df['BB%'] = 100 * ((batting_df['BB'] + batting_df['IBB']) / batting_df['PA'])

In [20]:
#Creating a Stolen Base Percentage column
batting_df['SB%'] = 100 * (batting_df['SB'] / (batting_df['SB'] + batting_df['CS'] ))

In [21]:
batting_df.tail(20)

playerID  yearID  stint teamID lgID    G   AB   R    H  2B  ...   SF  \
110475   yanghy01    2021      1    TEX   AL   12    0   0    0   0  ...  0.0   
110476  yarbrry01    2021      1    TBA   AL   30    4   0    0   0  ...  0.0   
110477  yardler01    2021      1    MIL   NL   17    0   0    0   0  ...  0.0   
110478  yastrmi01    2021      1    SFN   NL  139  468  75  105  28  ...  3.0   
110479  yelicch01    2021      1    MIL   NL  117  399  70   99  19  ...  3.0   
110480   ynoahu01    2021      1    ATL   NL   18   32   3    7   1  ...  0.0   
110481  youngal01    2021      1    ARI   NL   30    4   0    0   0  ...  0.0   
110482  youngal01    2021      2    CLE   AL   10    0   0    0   0  ...  0.0   
110483  youngan02    2021      1    ARI   NL   58   91  13   19   7  ...  1.0   
110484  zamorda01    2021      1    SEA   AL    4    0   0    0   0  ...  0.0   
110485  zavalse01    2021      1    CHA   AL   37   93  15   17   3  ...  0.0   
110486  zerpaan01    2021      1    KCA   AL    1    0   0    0   0  ...  0.0   
110487  zeuchtj01    2021      1    TOR   AL    5    0   0    0   0  ...  0.0   
110488  zimmebr01    2021      1    CLE   AL   99  299  44   68   9  ...  4.0   
110489  zimmebr02    2021      1    BAL   AL   14    4   0    0   0  ...  0.0   
110490  zimmejo02    2021      1    MIL   NL    2    1   0    0   0  ...  0.0   
110491  zimmeky01    2021      1    KCA   AL   52    0   0    0   0  ...  0.0   
110492  zimmery01    2021      1    WAS   NL  110  255  27   62  16  ...  2.0   
110493  zuberty01    2021      1    KCA   AL   31    1   0    0   0  ...  0.0   
110494  zuninmi01    2021      1    TBA   AL  109  333  64   72  11  ...  1.0   

        GIDP     PA       AVG       OBP       SLG       OPS          K%  \
110475   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110476   0.0    4.0  0.000000  0.000000  0.000000  0.000000   50.000000   
110477   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110478   3.0  536.0  0.224359  0.307836  0.457265  0.765101   24.440299   
110479   5.0  480.0  0.248120  0.358333  0.373434  0.731767   23.541667   
110480   0.0   32.0  0.218750  0.218750  0.437500  0.656250   46.875000   
110481   0.0    4.0  0.000000  0.000000  0.000000  0.000000  100.000000   
110482   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110483   3.0  104.0  0.208791  0.298077  0.483516  0.781593   43.269231   
110484   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110485   1.0  104.0  0.182796  0.230769  0.376344  0.607113   39.423077   
110486   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110487   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110488   3.0  348.0  0.227425  0.324713  0.344482  0.669194   35.057471   
110489   0.0    4.0  0.000000  0.000000  0.000000  0.000000   75.000000   
110490   0.0    1.0  0.000000  0.000000  0.000000  0.000000  100.000000   
110491   0.0    0.0       NaN       NaN       NaN       NaN         NaN   
110492   9.0  273.0  0.243137  0.285714  0.470588  0.756303   28.205128   
110493   0.0    1.0  0.000000  0.000000  0.000000  0.000000  100.000000   
110494   7.0  375.0  0.216216  0.301333  0.558559  0.859892   35.200000   

              BB%         SB%  
110475        NaN         NaN  
110476   0.000000         NaN  
110477        NaN         NaN  
110478  10.261194  100.000000  
110479  15.625000   75.000000  
110480   0.000000         NaN  
110481   0.000000         NaN  
110482        NaN         NaN  
110483   5.769231         NaN  
110484        NaN         NaN  
110485   5.769231         NaN  
110486        NaN         NaN  
110487        NaN         NaN  
110488   8.620690   83.333333  
110489   0.000000         NaN  
110490   0.000000         NaN  
110491        NaN         NaN  
110492   5.860806         NaN  
110493   0.000000         NaN  
110494   9.066667         NaN  

[20 rows x 30 columns]

In [22]:
batting_df['stint'].value_counts(normalize=True)

1    0.924911
2    0.070872
3    0.003937
4    0.000244
5    0.000036
Name: stint, dtype: float64

I can drop stint, I don't know what this column means (maybe how many times they were sent down and came back up? However with 92.5% of the data being 1's I feel safe dropping this column.  

In [23]:
batting_df_clean = batting_df.drop(['stint', 'PA','H', '2B', '3B', 'BB', 'SO', 'HBP', 'SH', 'SF', 'GIDP', 'IBB', 'CS'], axis=1) 

In [24]:
batting_df_clean.tail(10)

playerID  yearID teamID lgID    G   AB   R  HR   RBI    SB       AVG  \
110485  zavalse01    2021    CHA   AL   37   93  15   5  15.0   0.0  0.182796   
110486  zerpaan01    2021    KCA   AL    1    0   0   0   0.0   0.0       NaN   
110487  zeuchtj01    2021    TOR   AL    5    0   0   0   0.0   0.0       NaN   
110488  zimmebr01    2021    CLE   AL   99  299  44   8  35.0  15.0  0.227425   
110489  zimmebr02    2021    BAL   AL   14    4   0   0   0.0   0.0  0.000000   
110490  zimmejo02    2021    MIL   NL    2    1   0   0   0.0   0.0  0.000000   
110491  zimmeky01    2021    KCA   AL   52    0   0   0   0.0   0.0       NaN   
110492  zimmery01    2021    WAS   NL  110  255  27  14  46.0   0.0  0.243137   
110493  zuberty01    2021    KCA   AL   31    1   0   0   0.0   0.0  0.000000   
110494  zuninmi01    2021    TBA   AL  109  333  64  33  62.0   0.0  0.216216   

             OBP       SLG       OPS          K%       BB%        SB%  
110485  0.230769  0.376344  0.607113   39.423077  5.769231        NaN  
110486       NaN       NaN       NaN         NaN       NaN        NaN  
110487       NaN       NaN       NaN         NaN       NaN        NaN  
110488  0.324713  0.344482  0.669194   35.057471  8.620690  83.333333  
110489  0.000000  0.000000  0.000000   75.000000  0.000000        NaN  
110490  0.000000  0.000000  0.000000  100.000000  0.000000        NaN  
110491       NaN       NaN       NaN         NaN       NaN        NaN  
110492  0.285714  0.470588  0.756303   28.205128  5.860806        NaN  
110493  0.000000  0.000000  0.000000  100.000000  0.000000        NaN  
110494  0.301333  0.558559  0.859892   35.200000  9.066667        NaN

#### Cleaning people_df

In [25]:
people_df.tail(10)

playerID  birthYear  birthMonth  birthDay birthCountry birthState  \
20360  zuberty01     1995.0         6.0      16.0          USA         AR   
20361  zuletju01     1975.0         3.0      28.0       Panama     Panama   
20362  zumayjo01     1984.0        11.0       9.0          USA         CA   
20363  zuninmi01     1991.0         3.0      25.0          USA         FL   
20364  zupcibo01     1966.0         8.0      18.0          USA         PA   
20365   zupofr01     1939.0         8.0      29.0          USA         CA   
20366  zuvelpa01     1958.0        10.0      31.0          USA         CA   
20367  zuverge01     1924.0         8.0      20.0          USA         MI   
20368  zwilldu01     1888.0        11.0       2.0          USA         MO   
20369   zychto01     1990.0         8.0       7.0          USA         IL   

           birthCity  deathYear  deathMonth  deathDay  ...  nameLast  \
20360     White Hall        NaN         NaN       NaN  ...     Zuber   
20361         Panama        NaN         NaN       NaN  ...    Zuleta   
20362    Chula Vista        NaN         NaN       NaN  ...    Zumaya   
20363     Cape Coral        NaN         NaN       NaN  ...    Zunino   
20364     Pittsburgh        NaN         NaN       NaN  ...    Zupcic   
20365  San Francisco     2005.0         3.0      25.0  ...      Zupo   
20366      San Mateo        NaN         NaN       NaN  ...   Zuvella   
20367        Holland     2014.0         9.0       8.0  ...  Zuverink   
20368      St. Louis     1978.0         3.0      27.0  ...  Zwilling   
20369          Monee        NaN         NaN       NaN  ...      Zych   

             nameGiven weight height bats throws       debut   finalGame  \
20360       John Tyler  175.0   71.0    R      R  2020-07-24  2021-09-30   
20361    Julio Ernesto  230.0   78.0    R      R  2000-04-06  2001-06-25   
20362      Joel Martin  215.0   75.0    R      R  2006-04-03  2010-06-28   
20363  Michael Accorsi  235.0   74.0    R      R  2013-06-12  2021-10-03   
20364           Robert  220.0   76.0    R      R  1991-09-07  1994-08-04   
20365     Frank Joseph  182.0   71.0    L      R  1957-07-01  1961-05-09   
20366             Paul  173.0   72.0    R      R  1982-09-04  1991-05-02   
20367           George  195.0   76.0    R      R  1951-04-21  1959-06-15   
20368  Edward Harrison  160.0   66.0    L      L  1910-08-14  1916-07-12   
20369    Anthony Aaron  190.0   75.0    R      R  2015-09-04  2017-08-19   

        retroID    bbrefID  
20360  zubet001  zuberty01  
20361  zulej001  zuletju01  
20362  zumaj001  zumayjo01  
20363  zunim001  zuninmi01  
20364  zupcb001  zupcibo01  
20365  zupof101   zupofr01  
20366  zuvep001  zuvelpa01  
20367  zuveg101  zuverge01  
20368  zwild101  zwilldu01  
20369  zycht001   zychto01  

[10 rows x 24 columns]

In [26]:
people_df.columns

Index(['playerID', 'birthYear', 'birthMonth', 'birthDay', 'birthCountry',
       'birthState', 'birthCity', 'deathYear', 'deathMonth', 'deathDay',
       'deathCountry', 'deathState', 'deathCity', 'nameFirst', 'nameLast',
       'nameGiven', 'weight', 'height', 'bats', 'throws', 'debut', 'finalGame',
       'retroID', 'bbrefID'],
      dtype='object')

Can drop birth country, birth state, birth city, death year, death month, death day, death country, death state, death city, final game.

Need to do more research to see which id is used, I see playedID, retroID, and bbredID.  At first glance it seems like playerID and bbrefID are the same. Not sure if retroID is used for anything.

In [27]:
people_df.drop(['birthCountry','birthState', 'birthCity', 'deathYear', 'deathMonth', 'deathDay','deathCountry', 'deathState', 'deathCity', 'finalGame'], axis=1, inplace=True) 

In [28]:
people_df.tail(10)

playerID  birthYear  birthMonth  birthDay nameFirst  nameLast  \
20360  zuberty01     1995.0         6.0      16.0     Tyler     Zuber   
20361  zuletju01     1975.0         3.0      28.0     Julio    Zuleta   
20362  zumayjo01     1984.0        11.0       9.0      Joel    Zumaya   
20363  zuninmi01     1991.0         3.0      25.0      Mike    Zunino   
20364  zupcibo01     1966.0         8.0      18.0       Bob    Zupcic   
20365   zupofr01     1939.0         8.0      29.0     Frank      Zupo   
20366  zuvelpa01     1958.0        10.0      31.0      Paul   Zuvella   
20367  zuverge01     1924.0         8.0      20.0    George  Zuverink   
20368  zwilldu01     1888.0        11.0       2.0     Dutch  Zwilling   
20369   zychto01     1990.0         8.0       7.0      Tony      Zych   

             nameGiven  weight  height bats throws       debut   retroID  \
20360       John Tyler   175.0    71.0    R      R  2020-07-24  zubet001   
20361    Julio Ernesto   230.0    78.0    R      R  2000-04-06  zulej001   
20362      Joel Martin   215.0    75.0    R      R  2006-04-03  zumaj001   
20363  Michael Accorsi   235.0    74.0    R      R  2013-06-12  zunim001   
20364           Robert   220.0    76.0    R      R  1991-09-07  zupcb001   
20365     Frank Joseph   182.0    71.0    L      R  1957-07-01  zupof101   
20366             Paul   173.0    72.0    R      R  1982-09-04  zuvep001   
20367           George   195.0    76.0    R      R  1951-04-21  zuveg101   
20368  Edward Harrison   160.0    66.0    L      L  1910-08-14  zwild101   
20369    Anthony Aaron   190.0    75.0    R      R  2015-09-04  zycht001   

         bbrefID  
20360  zuberty01  
20361  zuletju01  
20362  zumayjo01  
20363  zuninmi01  
20364  zupcibo01  
20365   zupofr01  
20366  zuvelpa01  
20367  zuverge01  
20368  zwilldu01  
20369   zychto01

I am dropping birthMonth and birthDay because I am going to pull the year from debut and subtract it from birthYear to have debut age, and then will drop debut and birthYear.

Also dropping nameGiven because it is redundant.

In [29]:
people_df.drop(['birthMonth' , 'birthDay' , 'nameGiven'], axis=1, inplace=True)

In [30]:
people_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20370 entries, 0 to 20369
Data columns (total 11 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   playerID   20370 non-null  object 
 1   birthYear  20259 non-null  float64
 2   nameFirst  20333 non-null  object 
 3   nameLast   20370 non-null  object 
 4   weight     19554 non-null  float64
 5   height     19634 non-null  float64
 6   bats       19189 non-null  object 
 7   throws     19393 non-null  object 
 8   debut      20160 non-null  object 
 9   retroID    20321 non-null  object 
 10  bbrefID    20357 non-null  object 
dtypes: float64(3), object(8)
memory usage: 1.7+ MB


Creating a new column called debut age, and then will drop debut and birthYear.

In [31]:
people_df['DebutAge'] = pd.to_datetime(people_df['debut']).dt.year - people_df['birthYear']

In [32]:
people_df.tail()

playerID  birthYear nameFirst  nameLast  weight  height bats throws  \
20365   zupofr01     1939.0     Frank      Zupo   182.0    71.0    L      R   
20366  zuvelpa01     1958.0      Paul   Zuvella   173.0    72.0    R      R   
20367  zuverge01     1924.0    George  Zuverink   195.0    76.0    R      R   
20368  zwilldu01     1888.0     Dutch  Zwilling   160.0    66.0    L      L   
20369   zychto01     1990.0      Tony      Zych   190.0    75.0    R      R   

            debut   retroID    bbrefID  DebutAge  
20365  1957-07-01  zupof101   zupofr01      18.0  
20366  1982-09-04  zuvep001  zuvelpa01      24.0  
20367  1951-04-21  zuveg101  zuverge01      27.0  
20368  1910-08-14  zwild101  zwilldu01      22.0  
20369  2015-09-04  zycht001   zychto01      25.0

In [33]:
people_df.drop(['debut' , 'birthYear'], axis=1, inplace=True)

In [34]:
people_df.tail(10) 

playerID nameFirst  nameLast  weight  height bats throws   retroID  \
20360  zuberty01     Tyler     Zuber   175.0    71.0    R      R  zubet001   
20361  zuletju01     Julio    Zuleta   230.0    78.0    R      R  zulej001   
20362  zumayjo01      Joel    Zumaya   215.0    75.0    R      R  zumaj001   
20363  zuninmi01      Mike    Zunino   235.0    74.0    R      R  zunim001   
20364  zupcibo01       Bob    Zupcic   220.0    76.0    R      R  zupcb001   
20365   zupofr01     Frank      Zupo   182.0    71.0    L      R  zupof101   
20366  zuvelpa01      Paul   Zuvella   173.0    72.0    R      R  zuvep001   
20367  zuverge01    George  Zuverink   195.0    76.0    R      R  zuveg101   
20368  zwilldu01     Dutch  Zwilling   160.0    66.0    L      L  zwild101   
20369   zychto01      Tony      Zych   190.0    75.0    R      R  zycht001   

         bbrefID  DebutAge  
20360  zuberty01      25.0  
20361  zuletju01      25.0  
20362  zumayjo01      22.0  
20363  zuninmi01      22.0  
20364  zupcibo01      25.0  
20365   zupofr01      18.0  
20366  zuvelpa01      24.0  
20367  zuverge01      27.0  
20368  zwilldu01      22.0  
20369   zychto01      25.0

In [35]:
people_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 20370 entries, 0 to 20369
Data columns (total 10 columns):
 #   Column     Non-Null Count  Dtype  
---  ------     --------------  -----  
 0   playerID   20370 non-null  object 
 1   nameFirst  20333 non-null  object 
 2   nameLast   20370 non-null  object 
 3   weight     19554 non-null  float64
 4   height     19634 non-null  float64
 5   bats       19189 non-null  object 
 6   throws     19393 non-null  object 
 7   retroID    20321 non-null  object 
 8   bbrefID    20357 non-null  object 
 9   DebutAge   20051 non-null  float64
dtypes: float64(3), object(7)
memory usage: 1.6+ MB


In [36]:
(people_df['playerID'] == people_df['bbrefID']).sum()

20123

In [37]:
20123/20370

0.9878743249877271

98.8% of our playerID coulumn is a match to our bbrefID column.  Don't need this column and will be dropping it.

In [38]:
(people_df['playerID'] == people_df['retroID']).sum()

0

playerID and retroID have no rows in which they are equal.  Don't need retroID and will be dropping it.

In [39]:
people_df.drop(['bbrefID' , 'retroID'], axis=1, inplace=True)

Creating a new column called full_name and then dropping the nameFirst and nameLast columns.

In [40]:
people_df['full_name'] = (people_df['nameFirst'] + ' ' + people_df['nameLast'])

In [41]:
people_df.drop(['nameFirst' , 'nameLast'], axis=1, inplace=True)

In [42]:
people_df_clean = people_df

In [43]:
people_df.drop(['weight' , 'height' , 'bats' , 'throws'], axis=1, inplace=True)

In [44]:
people_df_clean.tail()

playerID  DebutAge        full_name
20365   zupofr01      18.0       Frank Zupo
20366  zuvelpa01      24.0     Paul Zuvella
20367  zuverge01      27.0  George Zuverink
20368  zwilldu01      22.0   Dutch Zwilling
20369   zychto01      25.0        Tony Zych

#### Cleaning allstar_df

In [45]:
allstar_df.tail(10)

playerID  yearID  gameNum        gameID teamID lgID  GP  startingPos
5444  reyesal02    2021        0  NLS202107130    SLN   NL   0          NaN
5445  rogertr01    2021        0  NLS202107130    MIA   NL   1          NaN
5446  schwaky01    2021        0  NLS202107130    WAS   NL   0          NaN
5447   sotoju01    2021        0  NLS202107130    WAS   NL   1          NaN
5448  tayloch03    2021        0  NLS202107130    LAN   NL   1          NaN
5449  turneju01    2021        0  NLS202107130    LAN   NL   1          NaN
5450  turnetr01    2021        0  NLS202107130    WAS   NL   1          NaN
5451  walketa01    2021        0  NLS202107130    NYN   NL   1          NaN
5452  wheelza01    2021        0  NLS202107130    PHI   NL   0          NaN
5453  woodrbr01    2021        0  NLS202107130    MIL   NL   0          NaN

In [46]:
allstar_df.columns

Index(['playerID', 'yearID', 'gameNum', 'gameID', 'teamID', 'lgID', 'GP',
       'startingPos'],
      dtype='object')

In [47]:
allstar_df['gameNum'].value_counts(normalize=True)

0    0.937110
2    0.033187
1    0.029703
Name: gameNum, dtype: float64

Can drop gameNum column because since I am only going to use data from 1990-present.  There hasn't been more than 1 All Star Game since 1962.

In [48]:
#Dropping the gameNum column
allstar_df.drop(['gameNum'], axis=1, inplace=True) 

In [49]:
allstar_df['startingPos'].value_counts(normalize=True)

8.0     0.108708
7.0     0.108708
6.0     0.108708
5.0     0.108708
4.0     0.108708
3.0     0.108708
2.0     0.108708
9.0     0.108124
1.0     0.106371
10.0    0.024547
Name: startingPos, dtype: float64

Wanted to make sure that the values in startingPos made sense, and they do.

In [50]:
allstar_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5454 entries, 0 to 5453
Data columns (total 7 columns):
 #   Column       Non-Null Count  Dtype  
---  ------       --------------  -----  
 0   playerID     5454 non-null   object 
 1   yearID       5454 non-null   int64  
 2   gameID       5405 non-null   object 
 3   teamID       5454 non-null   object 
 4   lgID         5454 non-null   object 
 5   GP           5454 non-null   int64  
 6   startingPos  1711 non-null   float64
dtypes: float64(1), int64(2), object(4)
memory usage: 298.4+ KB


startingPos will be a good way to see if a player started in an all star game or if they came off the bench (the NaN values).

In [51]:
allstar_df['GP'].value_counts(normalize=True)

1    0.779611
0    0.220389
Name: GP, dtype: float64

Whether or not someone actually played in the All Star Game isn't important, what's important is that they were on voted to make the team.  I feel safe dropping GP.

In [52]:
#Dropping the Game Played column
allstar_df.drop(['GP'], axis=1, inplace=True) 

In [53]:
allstar_df.tail()

playerID  yearID        gameID teamID lgID  startingPos
5449  turneju01    2021  NLS202107130    LAN   NL          NaN
5450  turnetr01    2021  NLS202107130    WAS   NL          NaN
5451  walketa01    2021  NLS202107130    NYN   NL          NaN
5452  wheelza01    2021  NLS202107130    PHI   NL          NaN
5453  woodrbr01    2021  NLS202107130    MIL   NL          NaN

I am dropping gameID, teamID, and lgID because this data will be found in other dataframes this will be merged on.

In [54]:
allstar_df.drop(['gameID','teamID','lgID'], axis=1, inplace=True)

In [55]:
allstar_df_clean = allstar_df

In [56]:
allstar_df_clean.tail(50)

playerID  yearID  startingPos
5404  pressry01    2021          NaN
5405  ramirjo01    2021          NaN
5406  rodonca01    2021          NaN
5407  rogerta01    2021          NaN
5408   sotogr01    2021          NaN
5409  troutmi01    2021          NaN
5410  walshja01    2021          NaN
5411  wendljo01    2021          NaN
5412  zuninmi01    2021          NaN
5413  scherma01    2021          1.0
5414  realmjt01    2021          2.0
5415  freemfr01    2021          3.0
5416  fraziad01    2021          4.0
5417  arenano01    2021          5.0
5418  tatisfe02    2021          6.0
5419  winkeje01    2021          7.0
5420  reynobr01    2021          8.0
5421  casteni01    2021          9.0
5422  muncyma01    2021         10.0
5423  acunaro01    2021          NaN
5424  albieoz01    2021          NaN
5425  bettsmo01    2021          NaN
5426  bryankr01    2021          NaN
5427  buehlwa01    2021          NaN
5428  burneco01    2021          NaN
5429  crawfbr01    2021          NaN
5430  croneja01    2021          NaN
5431  darviyu01    2021          NaN
5432  degroja01    2021          NaN
5433  escobed01    2021          NaN
5434  gausmke01    2021          NaN
5435  haderjo01    2021          NaN
5436  kimbrcr01    2021          NaN
5437  machama01    2021          NaN
5438  marquge01    2021          NaN
5439  melanma01    2021          NaN
5440  molinya01    2021          NaN
5441  narvaom01    2021          NaN
5442  peralfr01    2021          NaN
5443  poseybu01    2021          NaN
5444  reyesal02    2021          NaN
5445  rogertr01    2021          NaN
5446  schwaky01    2021          NaN
5447   sotoju01    2021          NaN
5448  tayloch03    2021          NaN
5449  turneju01    2021          NaN
5450  turnetr01    2021          NaN
5451  walketa01    2021          NaN
5452  wheelza01    2021          NaN
5453  woodrbr01    2021          NaN

In [57]:
allstar_df_clean['allstar'] = allstar_df_clean['startingPos'].isna()

In [58]:
allstar_df_clean

playerID  yearID  startingPos  allstar
0     gomezle01    1933          1.0    False
1     ferreri01    1933          2.0    False
2     gehrilo01    1933          3.0    False
3     gehrich01    1933          4.0    False
4     dykesji01    1933          5.0    False
...         ...     ...          ...      ...
5449  turneju01    2021          NaN     True
5450  turnetr01    2021          NaN     True
5451  walketa01    2021          NaN     True
5452  wheelza01    2021          NaN     True
5453  woodrbr01    2021          NaN     True

[5454 rows x 4 columns]

In [59]:
allstar_df_clean['allstar'] = allstar_df_clean['allstar'].astype(int)

In [60]:
allstar_df_clean

playerID  yearID  startingPos  allstar
0     gomezle01    1933          1.0        0
1     ferreri01    1933          2.0        0
2     gehrilo01    1933          3.0        0
3     gehrich01    1933          4.0        0
4     dykesji01    1933          5.0        0
...         ...     ...          ...      ...
5449  turneju01    2021          NaN        1
5450  turnetr01    2021          NaN        1
5451  walketa01    2021          NaN        1
5452  wheelza01    2021          NaN        1
5453  woodrbr01    2021          NaN        1

[5454 rows x 4 columns]

In [61]:
allstar_df_clean['allstar'].replace(0 , 1 , inplace=True)

In [62]:
allstar_df_clean['allstar_starter'] = allstar_df_clean['startingPos'].isna()

In [63]:
allstar_df_clean['allstar_starter'] = allstar_df_clean['allstar_starter'].map({False : 1 , True : 0})

In [64]:
allstar_df_clean.drop(['startingPos'], axis=1, inplace=True)

In [65]:
allstar_df_clean

playerID  yearID  allstar  allstar_starter
0     gomezle01    1933        1                1
1     ferreri01    1933        1                1
2     gehrilo01    1933        1                1
3     gehrich01    1933        1                1
4     dykesji01    1933        1                1
...         ...     ...      ...              ...
5449  turneju01    2021        1                0
5450  turnetr01    2021        1                0
5451  walketa01    2021        1                0
5452  wheelza01    2021        1                0
5453  woodrbr01    2021        1                0

[5454 rows x 4 columns]

#### Cleaning awards1_df

In [66]:
awards1_df.tail(10)

playerID         awardID  yearID lgID  tie notes
6521  albieoz01    TSN All-Star    2021   NL  NaN    2B
6522  machama01    TSN All-Star    2021   NL  NaN    3B
6523  tatisfe02    TSN All-Star    2021   NL  NaN    SS
6524   sotoju01    TSN All-Star    2021   NL  NaN    OF
6525  harpebr03    TSN All-Star    2021   NL  NaN    OF
6526  reynobr01    TSN All-Star    2021   NL  NaN    OF
6527  scherma01    TSN All-Star    2021   NL  NaN    SP
6528  haderjo01    TSN All-Star    2021   NL  NaN    RP
6529  friedma01  Silver Slugger    2021   NL  NaN     P
6530  ramirjo01    TSN All-Star    2021   AL  NaN    3B

In [67]:
awards1_df.columns

Index(['playerID', 'awardID', 'yearID', 'lgID', 'tie', 'notes'], dtype='object')

In [68]:
awards1_df['awardID'].value_counts()

Baseball Magazine All-Star             1520
TSN All-Star                           1477
Gold Glove                             1164
Silver Slugger                          752
Most Valuable Player                    204
Rookie of the Year                      150
TSN Pitcher of the Year                 137
Cy Young Award                          122
TSN Player of the Year                   92
TSN Fireman of the Year                  88
TSN Major League Player of the Year      82
Rolaids Relief Man Award                 74
World Series MVP                         69
Babe Ruth Award                          64
Lou Gehrig Memorial Award                57
All-Star Game MVP                        55
Roberto Clemente Award                   52
Hutch Award                              48
NLCS MVP                                 47
Hank Aaron Award                         46
ALCS MVP                                 41
Pitching Triple Crown                    38
TSN Guide MVP                   

Dropping awardID, lgID, tie, notes because I just want to use this data to know whether or not they player won an award, I don't care what the award was, the league, if they tied, or their position. 

In [69]:
awards1_df_clean = awards1_df.drop(['awardID', 'lgID', 'tie' , 'notes'], axis=1)

In [70]:
awards1_df_clean

playerID  yearID
0      bondto01    1877
1     hinespa01    1878
2     heckegu01    1884
3     radboch01    1884
4     oneilti01    1887
...         ...     ...
6526  reynobr01    2021
6527  scherma01    2021
6528  haderjo01    2021
6529  friedma01    2021
6530  ramirjo01    2021

[6531 rows x 2 columns]

In [71]:
awards1_df_clean['won_award'] = awards1_df_clean['yearID'].isna()

In [72]:
awards1_df_clean['won_award'] = awards1_df_clean['won_award'].astype(int)

In [73]:
awards1_df_clean['won_award'] = awards1_df_clean['won_award'].map({False : 1 , True : 0})

In [74]:
awards1_df_clean

playerID  yearID  won_award
0      bondto01    1877          1
1     hinespa01    1878          1
2     heckegu01    1884          1
3     radboch01    1884          1
4     oneilti01    1887          1
...         ...     ...        ...
6526  reynobr01    2021          1
6527  scherma01    2021          1
6528  haderjo01    2021          1
6529  friedma01    2021          1
6530  ramirjo01    2021          1

[6531 rows x 3 columns]

#### Cleaning awards2_df

In [75]:
awards2_df.tail(10)

awardID  yearID lgID   playerID  pointsWon  pointsMax  \
6869  Rookie of the Year    2016   AL  mazarno01        4.0        150   
6870  Rookie of the Year    2016   AL  anderti01        2.0        150   
6871  Rookie of the Year    2016   NL  seageco01      150.0        150   
6872  Rookie of the Year    2016   NL  turnetr01       42.0        150   
6873  Rookie of the Year    2016   NL  maedake01       37.0        150   
6874  Rookie of the Year    2016   NL  storytr01       24.0        150   
6875  Rookie of the Year    2016   NL   diazal02       14.0        150   
6876  Rookie of the Year    2016   NL   grayjo02        1.0        150   
6877  Rookie of the Year    2016   NL   matzst01        1.0        150   
6878  Rookie of the Year    2016   NL     ohse01        1.0        150   

      votesFirst  
6869         0.0  
6870         0.0  
6871        30.0  
6872         0.0  
6873         0.0  
6874         0.0  
6875         0.0  
6876         0.0  
6877         0.0  
6878         0.0

In [76]:
awards2_df.columns

Index(['awardID', 'yearID', 'lgID', 'playerID', 'pointsWon', 'pointsMax',
       'votesFirst'],
      dtype='object')

In [77]:
awards2_df['awardID'].value_counts()

MVP                   5263
Rookie of the Year     831
Cy Young               785
Name: awardID, dtype: int64

Awards 2 includes the 3 biggest individual awards.  I will use awards 1 to show if a player has won any type of award, I will use awards 2 to show if they won one of the 3 biggest awards in MLB, or got any votes at all.

In [78]:
awards2_df_clean = awards2_df.drop(['pointsMax' , 'votesFirst', 'lgID'], axis=1)

In [79]:
awards2_df_clean.tail(10)

awardID  yearID   playerID  pointsWon
6869  Rookie of the Year    2016  mazarno01        4.0
6870  Rookie of the Year    2016  anderti01        2.0
6871  Rookie of the Year    2016  seageco01      150.0
6872  Rookie of the Year    2016  turnetr01       42.0
6873  Rookie of the Year    2016  maedake01       37.0
6874  Rookie of the Year    2016  storytr01       24.0
6875  Rookie of the Year    2016   diazal02       14.0
6876  Rookie of the Year    2016   grayjo02        1.0
6877  Rookie of the Year    2016   matzst01        1.0
6878  Rookie of the Year    2016     ohse01        1.0

In [80]:
awards2_df_clean['award_votes'] = awards2_df_clean['pointsWon'].isna()

In [81]:
awards2_df_clean['award_votes'] = awards2_df_clean['award_votes'].astype(int)

In [82]:
awards2_df_clean['award_votes'].replace(0 , 1 , inplace=True)

In [83]:
awards2_df_clean = awards2_df_clean.drop(['awardID' , 'pointsWon'], axis=1)

In [84]:
awards2_df_clean.drop_duplicates()

yearID   playerID  award_votes
0       1956   fordwh01            1
1       1956  maglisa01            1
2       1956  newcodo01            1
3       1956  spahnwa01            1
4       1957  donovdi01            1
...      ...        ...          ...
6874    2016  storytr01            1
6875    2016   diazal02            1
6876    2016   grayjo02            1
6877    2016   matzst01            1
6878    2016     ohse01            1

[6270 rows x 3 columns]

#### Cleaning salaries_df

In [85]:
salaries_df.tail(10)

yearID teamID lgID   playerID    salary
26418    2016    WAS   NL  riverfe01    516100
26419    2016    WAS   NL  roarkta01    543400
26420    2016    WAS   NL  robincl01    534900
26421    2016    WAS   NL   rossjo01    514400
26422    2016    WAS   NL  scherma01  22142857
26423    2016    WAS   NL  strasst01  10400000
26424    2016    WAS   NL  taylomi02    524000
26425    2016    WAS   NL  treinbl01    524900
26426    2016    WAS   NL  werthja01  21733615
26427    2016    WAS   NL  zimmery01  14000000

In [86]:
salaries_df.shape

(26428, 5)

In [87]:
salaries_df_clean = salaries_df.drop(['teamID' , 'lgID'], axis=1)

In [88]:
salaries_df_clean.tail(10)

yearID   playerID    salary
26418    2016  riverfe01    516100
26419    2016  roarkta01    543400
26420    2016  robincl01    534900
26421    2016   rossjo01    514400
26422    2016  scherma01  22142857
26423    2016  strasst01  10400000
26424    2016  taylomi02    524000
26425    2016  treinbl01    524900
26426    2016  werthja01  21733615
26427    2016  zimmery01  14000000

In [89]:
salaries_df_clean = salaries_df_clean[(salaries_df_clean['yearID']>= 1996) & (salaries_df_clean['yearID']<= 2016)]

In [90]:
salaries_df_clean['yearID'].value_counts()

1999    1006
1998     998
1996     931
1997     925
2001     860
2008     856
2016     853
2012     848
2002     846
2007     842
2011     839
2000     836
2005     831
2004     831
2010     830
2003     827
2006     819
2015     817
2013     815
2009     813
2014     802
Name: yearID, dtype: int64

#### Cleaning salary2_df

In [91]:
salary2_df

full_name       salary2  yearID  Unnamed: 3  Unnamed: 4  \
0        Albert Belle  $12,868,670     2000         NaN         NaN   
1     Bernie Williams  $12,357,143     2000         NaN         NaN   
2        Larry Walker  $12,142,857     2000         NaN         NaN   
3         Mike Piazza  $12,071,429     2000         NaN         NaN   
4           Mo Vaughn  $11,166,667     2000         NaN         NaN   
...               ...           ...     ...         ...         ...   
9285   Chas McCormick     $570,500     2021         NaN         NaN   
9286       Jose Rojas     $570,500     2021         NaN         NaN   
9287        Ka'ai Tom     $570,500     2021         NaN         NaN   
9288  Taylor Trammell     $570,500     2021         NaN         NaN   
9289    Andrew Vaughn     $570,500     2021         NaN         NaN   

      Unnamed: 5  Unnamed: 6  Unnamed: 7  Unnamed: 8  Unnamed: 9  ...  \
0            NaN         NaN         NaN         NaN         NaN  ...   
1            NaN         NaN         NaN         NaN         NaN  ...   
2            NaN         NaN         NaN         NaN         NaN  ...   
3            NaN         NaN         NaN         NaN         NaN  ...   
4            NaN         NaN         NaN         NaN         NaN  ...   
...          ...         ...         ...         ...         ...  ...   
9285         NaN         NaN         NaN         NaN         NaN  ...   
9286         NaN         NaN         NaN         NaN         NaN  ...   
9287         NaN         NaN         NaN         NaN         NaN  ...   
9288         NaN         NaN         NaN         NaN         NaN  ...   
9289         NaN         NaN         NaN         NaN         NaN  ...   

      Unnamed: 15  Unnamed: 16  Unnamed: 17  Unnamed: 18  Unnamed: 19  \
0             NaN          NaN          NaN          NaN          NaN   
1             NaN          NaN          NaN          NaN          NaN   
2             NaN          NaN          NaN          NaN          NaN   
3             NaN          NaN          NaN          NaN          NaN   
4             NaN          NaN          NaN          NaN          NaN   
...           ...          ...          ...          ...          ...   
9285          NaN          NaN          NaN          NaN          NaN   
9286          NaN          NaN          NaN          NaN          NaN   
9287          NaN          NaN          NaN          NaN          NaN   
9288          NaN          NaN          NaN          NaN          NaN   
9289          NaN          NaN          NaN          NaN          NaN   

      Unnamed: 20  Unnamed: 21  Unnamed: 22  Unnamed: 23  Unnamed: 24  
0             NaN          NaN          NaN          NaN          NaN  
1             NaN          NaN          NaN          NaN          NaN  
2             NaN          NaN          NaN          NaN          NaN  
3             NaN          NaN          NaN          NaN          NaN  
4             NaN          NaN          NaN          NaN          NaN  
...           ...          ...          ...          ...          ...  
9285          NaN          NaN          NaN          NaN          NaN  
9286          NaN          NaN          NaN          NaN          NaN  
9287          NaN          NaN          NaN          NaN          NaN  
9288          NaN          NaN          NaN          NaN          NaN  
9289          NaN          NaN          NaN          NaN          NaN  

[9290 rows x 25 columns]

In [92]:
salary2_df.columns

Index(['full_name', 'salary2', 'yearID', 'Unnamed: 3', 'Unnamed: 4',
       'Unnamed: 5', 'Unnamed: 6', 'Unnamed: 7', 'Unnamed: 8', 'Unnamed: 9',
       'Unnamed: 10', 'Unnamed: 11', 'Unnamed: 12', 'Unnamed: 13',
       'Unnamed: 14', 'Unnamed: 15', 'Unnamed: 16', 'Unnamed: 17',
       'Unnamed: 18', 'Unnamed: 19', 'Unnamed: 20', 'Unnamed: 21',
       'Unnamed: 22', 'Unnamed: 23', 'Unnamed: 24'],
      dtype='object')

In [93]:
salary2_df_clean = salary2_df.drop(['Unnamed: 3', 'Unnamed: 4',
       'Unnamed: 5', 'Unnamed: 6', 'Unnamed: 7', 'Unnamed: 8', 'Unnamed: 9',
       'Unnamed: 10', 'Unnamed: 11', 'Unnamed: 12', 'Unnamed: 13',
       'Unnamed: 14', 'Unnamed: 15', 'Unnamed: 16', 'Unnamed: 17',
       'Unnamed: 18', 'Unnamed: 19', 'Unnamed: 20', 'Unnamed: 21',
       'Unnamed: 22', 'Unnamed: 23', 'Unnamed: 24'], axis=1)

In [94]:
salary2_df_clean

full_name       salary2  yearID
0        Albert Belle  $12,868,670     2000
1     Bernie Williams  $12,357,143     2000
2        Larry Walker  $12,142,857     2000
3         Mike Piazza  $12,071,429     2000
4           Mo Vaughn  $11,166,667     2000
...               ...           ...     ...
9285   Chas McCormick     $570,500     2021
9286       Jose Rojas     $570,500     2021
9287        Ka'ai Tom     $570,500     2021
9288  Taylor Trammell     $570,500     2021
9289    Andrew Vaughn     $570,500     2021

[9290 rows x 3 columns]

#### Cleaning salary3_df

In [95]:
salary3_df

firstname lastname      full_name  yearID  salary
0         David  Aardsma  David Aardsma    2004  300000
1         David  Aardsma  David Aardsma    2006  327000
2         David  Aardsma  David Aardsma    2007  387500
3         David  Aardsma  David Aardsma    2008  403250
4         David  Aardsma  David Aardsma    2009  419000
...         ...      ...            ...     ...     ...
45491      Paul  Zuvella   Paul Zuvella    1988   62500
45492      Paul  Zuvella   Paul Zuvella    1989  145000
45493      Tony     Zych      Tony Zych    2015  507500
45494      Tony     Zych      Tony Zych    2016  511000
45495      Tony     Zych      Tony Zych    2017  539600

[45496 rows x 5 columns]

In [96]:
salary3_df_clean = salary3_df.drop(['firstname', 'lastname'], axis=1)

In [97]:
salary3_df_clean

full_name  yearID  salary
0      David Aardsma    2004  300000
1      David Aardsma    2006  327000
2      David Aardsma    2007  387500
3      David Aardsma    2008  403250
4      David Aardsma    2009  419000
...              ...     ...     ...
45491   Paul Zuvella    1988   62500
45492   Paul Zuvella    1989  145000
45493      Tony Zych    2015  507500
45494      Tony Zych    2016  511000
45495      Tony Zych    2017  539600

[45496 rows x 3 columns]

#### Cleaning teams_df

In [98]:
teams_df.tail(30)

yearID lgID teamID franchID divID  Rank    G  Ghome    W    L  ...   DP  \
2955    2021   NL    ARI      ARI     W     5  162   81.0   52  110  ...  113   
2956    2021   NL    ATL      ATL     E     1  161   80.0   88   73  ...  104   
2957    2021   AL    BAL      BAL     E     5  162   81.0   52  110  ...  101   
2958    2021   AL    BOS      BOS     E     2  162   81.0   92   70  ...  143   
2959    2021   AL    CHA      CHW     C     1  162   81.0   93   69  ...  112   
2960    2021   NL    CHN      CHC     C     4  162   81.0   71   91  ...  149   
2961    2021   NL    CIN      CIN     C     3  162   81.0   83   79  ...  124   
2962    2021   AL    CLE      CLE     C     2  162   81.0   80   82  ...  138   
2963    2021   NL    COL      COL     W     4  161   81.0   74   87  ...  140   
2964    2021   AL    DET      DET     C     3  162   81.0   77   85  ...  136   
2965    2021   AL    HOU      HOU     W     1  162   81.0   95   67  ...  126   
2966    2021   AL    KCA      KCR     C     4  162   81.0   74   88  ...  152   
2967    2021   AL    LAA      ANA     W     4  162   82.0   77   85  ...  131   
2968    2021   NL    LAN      LAD     W     2  162   81.0  106   56  ...   94   
2969    2021   NL    MIA      FLA     E     4  162   81.0   67   95  ...  146   
2970    2021   NL    MIL      MIL     C     1  162   81.0   95   67  ...  102   
2971    2021   AL    MIN      MIN     C     5  162   81.0   73   89  ...  138   
2972    2021   AL    NYA      NYY     E     2  162   81.0   92   70  ...  112   
2973    2021   NL    NYN      NYM     E     3  162   81.0   77   85  ...  121   
2974    2021   AL    OAK      OAK     W     3  162   81.0   86   76  ...  116   
2975    2021   NL    PHI      PHI     E     2  162   81.0   82   80  ...  142   
2976    2021   NL    PIT      PIT     C     5  162   81.0   61  101  ...  139   
2977    2021   NL    SDN      SDP     W     3  162   81.0   79   83  ...  139   
2978    2021   AL    SEA      SEA     W     2  162   81.0   90   72  ...  135   
2979    2021   NL    SFN      SFG     W     1  162   81.0  107   55  ...  122   
2980    2021   NL    SLN      STL     C     2  162   81.0   90   72  ...  137   
2981    2021   AL    TBA      TBD     E     1  162   81.0  100   62  ...  130   
2982    2021   AL    TEX      TEX     W     5  162   81.0   60  102  ...  146   
2983    2021   AL    TOR      TOR     E     4  162   80.0   91   71  ...  122   
2984    2021   NL    WAS      WSN     E     5  162   81.0   65   97  ...  116   

         FP                           name                         park  \
2955  0.983           Arizona Diamondbacks                  Chase Field   
2956  0.988                 Atlanta Braves                SunTrust Park   
2957  0.987              Baltimore Orioles  Oriole Park at Camden Yards   
2958  0.981                 Boston Red Sox               Fenway Park II   
2959  0.982              Chicago White Sox        Guaranteed Rate Field   
2960  0.985                   Chicago Cubs                Wrigley Field   
2961  0.984                Cincinnati Reds     Great American Ball Park   
2962  0.985              Cleveland Indians            Progressive Field   
2963  0.987               Colorado Rockies                  Coors Field   
2964  0.986                 Detroit Tigers                Comerica Park   
2965  0.988                 Houston Astros             Minute Maid Park   
2966  0.985             Kansas City Royals             Kauffman Stadium   
2967  0.985  Los Angeles Angels of Anaheim     Angel Stadium of Anaheim   
2968  0.985            Los Angeles Dodgers               Dodger Stadium   
2969  0.979                  Miami Marlins                 Marlins Park   
2970  0.984              Milwaukee Brewers                  Miller Park   
2971  0.982                Minnesota Twins                 Target Field   
2972  0.983               New York Yankees           Yankee Stadium III   
2973  0.983                  New York Mets                   Citi Fie

In [99]:
teams_df.columns

Index(['yearID', 'lgID', 'teamID', 'franchID', 'divID', 'Rank', 'G', 'Ghome',
       'W', 'L', 'DivWin', 'WCWin', 'LgWin', 'WSWin', 'R', 'AB', 'H', '2B',
       '3B', 'HR', 'BB', 'SO', 'SB', 'CS', 'HBP', 'SF', 'RA', 'ER', 'ERA',
       'CG', 'SHO', 'SV', 'IPouts', 'HA', 'HRA', 'BBA', 'SOA', 'E', 'DP', 'FP',
       'name', 'park', 'attendance', 'BPF', 'PPF', 'teamIDBR',
       'teamIDlahman45', 'teamIDretro'],
      dtype='object')

Can drop 'G', 'Ghome', 'R', 'AB', 'H', '2B','3B', 'HR', 'BB', 'SO', 'SB', 'CS', 'HBP', 'SF', 'RA', 'ER', 'ERA', 'CG', 'SHO', 'SV', 'IPouts', 'HA', 'HRA', 'BBA', 'SOA', 'E', 'DP', 'FP', 'name', 'park', 'attendance', 'BPF', 'PPF', 'teamIDBR', 'teamIDlahman45', 'teamIDretro'

I have to decide which of playoff_results_df and teams_df will be better suited to pair to each player to designate whether or not that player was on a winning team.

In [100]:
teams_df_clean = teams_df.drop(['G', 'Ghome', 'R', 'AB', 'H', '2B','3B', 'HR', 'BB', 'SO', 'SB', 'CS', 'HBP', 'SF', 'RA', 'ER', 'ERA', 'CG', 'SHO', 'SV', 'IPouts', 'HA', 'HRA', 'BBA', 'SOA', 'E', 'DP', 'FP', 'name', 'park', 'attendance', 'BPF', 'PPF', 'teamIDBR', 'teamIDlahman45', 'teamIDretro'], axis=1)

In [101]:
teams_df_clean.tail(10)

yearID lgID teamID franchID divID  Rank    W    L DivWin WCWin LgWin  \
2975    2021   NL    PHI      PHI     E     2   82   80      N     N     N   
2976    2021   NL    PIT      PIT     C     5   61  101      N     N     N   
2977    2021   NL    SDN      SDP     W     3   79   83      N     N     N   
2978    2021   AL    SEA      SEA     W     2   90   72      N     N     N   
2979    2021   NL    SFN      SFG     W     1  107   55      Y     N     N   
2980    2021   NL    SLN      STL     C     2   90   72      N     Y     N   
2981    2021   AL    TBA      TBD     E     1  100   62      Y     N     N   
2982    2021   AL    TEX      TEX     W     5   60  102      N     N     N   
2983    2021   AL    TOR      TOR     E     4   91   71      N     N     N   
2984    2021   NL    WAS      WSN     E     5   65   97      N     N     N   

     WSWin  
2975     N  
2976     N  
2977     N  
2978     N  
2979     N  
2980     N  
2981     N  
2982     N  
2983     N  
2984     N

Also need to drop 'franchID' , 'divID' , 'Rank' , 'W' , 'L' because I just want information on whether the team won the division, made the playoffs, made the World Series, or won the World Series.

In [102]:
teams_df_clean.drop(['franchID' , 'divID' , 'Rank' , 'W' , 'L'], axis=1, inplace=True)

In [103]:
teams_df_clean.tail()

yearID lgID teamID DivWin WCWin LgWin WSWin
2980    2021   NL    SLN      N     Y     N     N
2981    2021   AL    TBA      Y     N     N     N
2982    2021   AL    TEX      N     N     N     N
2983    2021   AL    TOR      N     N     N     N
2984    2021   NL    WAS      N     N     N     N

### Merging Dataframes

In [104]:
df_merged = batting_df_clean.merge(people_df_clean, how='left', on='playerID')

In [105]:
df_merged.tail()

playerID  yearID teamID lgID    G   AB   R  HR   RBI   SB       AVG  \
110490  zimmejo02    2021    MIL   NL    2    1   0   0   0.0  0.0  0.000000   
110491  zimmeky01    2021    KCA   AL   52    0   0   0   0.0  0.0       NaN   
110492  zimmery01    2021    WAS   NL  110  255  27  14  46.0  0.0  0.243137   
110493  zuberty01    2021    KCA   AL   31    1   0   0   0.0  0.0  0.000000   
110494  zuninmi01    2021    TBA   AL  109  333  64  33  62.0  0.0  0.216216   

             OBP       SLG       OPS          K%       BB%  SB%  DebutAge  \
110490  0.000000  0.000000  0.000000  100.000000  0.000000  NaN      23.0   
110491       NaN       NaN       NaN         NaN       NaN  NaN      28.0   
110492  0.285714  0.470588  0.756303   28.205128  5.860806  NaN      21.0   
110493  0.000000  0.000000  0.000000  100.000000  0.000000  NaN      25.0   
110494  0.301333  0.558559  0.859892   35.200000  9.066667  NaN      22.0   

                full_name  
110490  Jordan Zimmermann  
110491        Kyle Zimmer  
110492     Ryan Zimmerman  
110493        Tyler Zuber  
110494        Mike Zunino

In [106]:
df_merged = df_merged.merge(allstar_df_clean, how='left', on=['playerID', 'yearID'])

In [107]:
df_merged

playerID  yearID teamID lgID    G   AB   R  HR   RBI   SB  ...  \
0       abercda01    1871    TRO  NaN    1    4   0   0   0.0  0.0  ...   
1        addybo01    1871    RC1  NaN   25  118  30   0  13.0  8.0  ...   
2       allisar01    1871    CL1  NaN   29  137  28   0  19.0  3.0  ...   
3       allisdo01    1871    WS3  NaN   27  133  28   2  27.0  1.0  ...   
4       ansonca01    1871    RC1  NaN   25  120  29   0  16.0  6.0  ...   
...           ...     ...    ...  ...  ...  ...  ..  ..   ...  ...  ...   
110704  zimmejo02    2021    MIL   NL    2    1   0   0   0.0  0.0  ...   
110705  zimmeky01    2021    KCA   AL   52    0   0   0   0.0  0.0  ...   
110706  zimmery01    2021    WAS   NL  110  255  27  14  46.0  0.0  ...   
110707  zuberty01    2021    KCA   AL   31    1   0   0   0.0  0.0  ...   
110708  zuninmi01    2021    TBA   AL  109  333  64  33  62.0  0.0  ...   

             OBP       SLG       OPS          K%       BB%        SB%  \
0            NaN  0.000000       NaN         NaN       NaN        NaN   
1            NaN  0.322034       NaN         NaN       NaN  88.888889   
2            NaN  0.394161       NaN         NaN       NaN  75.000000   
3            NaN  0.481203       NaN         NaN       NaN  50.000000   
4            NaN  0.466667       NaN         NaN       NaN  75.000000   
...          ...       ...       ...         ...       ...        ...   
110704  0.000000  0.000000  0.000000  100.000000  0.000000        NaN   
110705       NaN       NaN       NaN         NaN       NaN        NaN   
110706  0.285714  0.470588  0.756303   28.205128  5.860806        NaN   
110707  0.000000  0.000000  0.000000  100.000000  0.000000        NaN   
110708  0.301333  0.558559  0.859892   35.200000  9.066667        NaN   

        DebutAge          full_name allstar  allstar_starter  
0           21.0  Frank Abercrombie     NaN              NaN  
1           29.0           Bob Addy     NaN              NaN  
2           22.0        Art Allison     NaN              NaN  
3           25.0       Doug Allison     NaN              NaN  
4           19.0          Cap Anson     NaN              NaN  
...          ...                ...     ...              ...  
110704      23.0  Jordan Zimmermann     NaN              NaN  
110705      28.0        Kyle Zimmer     NaN              NaN  
110706      21.0     Ryan Zimmerman     NaN              NaN  
110707      25.0        Tyler Zuber     NaN              NaN  
110708      22.0        Mike Zunino     1.0              0.0  

[110709 rows x 21 columns]

In [108]:
df_merged = df_merged.merge(awards1_df_clean, how='left', on=['playerID', 'yearID'])

In [109]:
#Checking to make sure that the merge is working properly, it is!
df_merged[df_merged['playerID'] == 'ramirjo01']

playerID  yearID teamID lgID    G   AB    R  HR    RBI    SB  ...  \
100801  ramirjo01    2013    CLE   AL   15   12    5   0    0.0   0.0  ...   
102219  ramirjo01    2014    CLE   AL   68  237   27   2   17.0  10.0  ...   
103705  ramirjo01    2015    CLE   AL   97  315   50   6   27.0  10.0  ...   
105208  ramirjo01    2016    CLE   AL  152  565   84  11   76.0  22.0  ...   
106716  ramirjo01    2017    CLE   AL  152  585  107  29   83.0  17.0  ...   
108263  ramirjo01    2018    CLE   AL  157  578  110  39  105.0  34.0  ...   
108264  ramirjo01    2018    CLE   AL  157  578  110  39  105.0  34.0  ...   
109838  ramirjo01    2019    CLE   AL  129  482   68  23   83.0  24.0  ...   
111302  ramirjo01    2020    CLE   AL   58  219   45  17   46.0  10.0  ...   
111303  ramirjo01    2020    CLE   AL   58  219   45  17   46.0  10.0  ...   
112926  ramirjo01    2021    CLE   AL  152  552  111  36  103.0  27.0  ...   

             SLG       OPS         K%        BB%        SB%  DebutAge  \
100801  0.500000  0.928571  14.285714  14.285714   0.000000      21.0   
102219  0.345992  0.631706  13.157895   4.887218  90.909091      21.0   
103705  0.339683  0.627006  10.985915   9.014085  71.428571      21.0   
105208  0.461947  0.823821  10.016155   7.269790  75.862069      21.0   
106716  0.582906  0.953675  10.615385   8.769231  77.272727      21.0   
108263  0.551903  0.930585  11.220196  16.970547  85.000000      21.0   
108264  0.551903  0.930585  11.220196  16.970547  85.000000      21.0   
109838  0.479253  0.804024  13.577982  10.091743  85.714286      21.0   
111302  0.607306  0.993133  16.929134  12.204724  76.923077      21.0   
111303  0.607306  0.993133  16.929134  12.204724  76.923077      21.0   
112926  0.538043  0.887889  13.467492  12.693498  87.096774      21.0   

           full_name  allstar allstar_starter  won_award  
100801  Jose Ramirez      NaN             NaN        NaN  
102219  Jose Ramirez      NaN             NaN        NaN  
103705  Jose Ramirez      NaN             NaN        NaN  
105208  Jose Ramirez      NaN             NaN        NaN  
106716  Jose Ramirez      1.0             1.0        1.0  
108263  Jose Ramirez      1.0             1.0        1.0  
108264  Jose Ramirez      1.0             1.0        1.0  
109838  Jose Ramirez      NaN             NaN        NaN  
111302  Jose Ramirez      NaN             NaN        1.0  
111303  Jose Ramirez      NaN             NaN        1.0  
112926  Jose Ramirez      1.0             0.0        1.0  

[11 rows x 22 columns]

In [110]:
df_merged.shape

(113410, 22)

In [111]:
df_merged = df_merged.merge(awards2_df_clean, how='left', on=['playerID', 'yearID'])

In [112]:
df_merged.shape

(114419, 23)

In [113]:
df_merged[df_merged['playerID'] == 'seageco01']

playerID  yearID teamID lgID    G   AB    R  HR   RBI   SB  ...  \
104845  seageco01    2015    LAN   NL   27   98   17   4  17.0  2.0  ...   
106368  seageco01    2016    LAN   NL  157  627  105  26  72.0  3.0  ...   
106369  seageco01    2016    LAN   NL  157  627  105  26  72.0  3.0  ...   
106370  seageco01    2016    LAN   NL  157  627  105  26  72.0  3.0  ...   
106371  seageco01    2016    LAN   NL  157  627  105  26  72.0  3.0  ...   
106372  seageco01    2016    LAN   NL  157  627  105  26  72.0  3.0  ...   
106373  seageco01    2016    LAN   NL  157  627  105  26  72.0  3.0  ...   
107871  seageco01    2017    LAN   NL  145  539   85  22  77.0  4.0  ...   
107872  seageco01    2017    LAN   NL  145  539   85  22  77.0  4.0  ...   
109410  seageco01    2018    LAN   NL   26  101   13   2  13.0  0.0  ...   
110992  seageco01    2019    LAN   NL  134  489   82  19  87.0  1.0  ...   
112420  seageco01    2020    LAN   NL   52  212   38  15  41.0  1.0  ...   
112421  seageco01    2020    LAN   NL   52  212   38  15  41.0  1.0  ...   
114088  seageco01    2021    LAN   NL   95  353   54  16  57.0  1.0  ...   

             OPS         K%        BB%         SB%  DebutAge     full_name  \
104845  0.982277  16.666667  13.157895  100.000000      21.0  Corey Seager   
106368  0.874678  19.219653   8.526012   50.000000      21.0  Corey Seager   
106369  0.874678  19.219653   8.526012   50.000000      21.0  Corey Seager   
106370  0.874678  19.219653   8.526012   50.000000      21.0  Corey Seager   
106371  0.874678  19.219653   8.526012   50.000000      21.0  Corey Seager   
106372  0.874678  19.219653   8.526012   50.000000      21.0  Corey Seager   
106373  0.874678  19.219653   8.526012   50.000000      21.0  Corey Seager   
107871  0.850832  21.197411  11.650485   66.666667      21.0  Corey Seager   
107872  0.850832  21.197411  11.650485   66.666667      21.0  Corey Seager   
109410  0.740867  14.655172  10.344828         NaN      21.0  Corey Seager   
110992  0.815338  18.014706   8.639706  100.000000      21.0  Corey Seager   
112420  0.942664  15.948276   7.327586  100.000000      21.0  Corey Seager   
112421  0.942664  15.948276   7.327586  100.000000      21.0  Corey Seager   
114088  0.912974  16.058394  12.165450   50.000000      21.0  Corey Seager   

        allstar  allstar_starter won_award  award_votes  
104845      NaN              NaN       NaN          NaN  
106368      1.0              0.0       1.0          1.0  
106369      1.0              0.0       1.0          1.0  
106370      1.0              0.0       1.0          1.0  
106371      1.0              0.0       1.0          1.0  
106372      1.0              0.0       1.0          1.0  
106373      1.0              0.0       1.0          1.0  
107871      1.0              0.0       1.0          NaN  
107872      1.0              0.0       1.0          NaN  
109410      NaN              NaN       NaN          NaN  
110992      NaN              NaN       NaN          NaN  
112420      NaN              NaN       1.0          NaN  
112421      NaN              NaN       1.0          NaN  
114088      NaN              NaN       NaN          NaN  

[14 rows x 23 columns]

In [114]:
df_merged = df_merged.merge(salaries_df_clean, how='left', on=['playerID', 'yearID'])

In [115]:
df_merged[df_merged['playerID'] == 'zimmery01']

playerID  yearID teamID lgID    G   AB    R  HR    RBI    SB  ...  \
90820   zimmery01    2005    WAS   NL   20   58    6   0    6.0   0.0  ...   
92237   zimmery01    2006    WAS   NL  157  614   84  20  110.0  11.0  ...   
93676   zimmery01    2007    WAS   NL  162  653   99  24   91.0   4.0  ...   
95094   zimmery01    2008    WAS   NL  106  428   51  14   51.0   1.0  ...   
96512   zimmery01    2009    WAS   NL  157  610  110  33  106.0   2.0  ...   
96513   zimmery01    2009    WAS   NL  157  610  110  33  106.0   2.0  ...   
97904   zimmery01    2010    WAS   NL  142  525   85  25   85.0   4.0  ...   
99332   zimmery01    2011    WAS   NL  101  395   52  12   49.0   3.0  ...   
100777  zimmery01    2012    WAS   NL  145  578   93  25   95.0   5.0  ...   
102210  zimmery01    2013    WAS   NL  147  568   84  26   79.0   6.0  ...   
103666  zimmery01    2014    WAS   NL   61  214   26   5   38.0   0.0  ...   
105176  zimmery01    2015    WAS   NL   95  346   43  16   73.0   1.0  ...   
106712  zimmery01    2016    WAS   NL  115  427   60  15   46.0   4.0  ...   
108233  zimmery01    2017    WAS   NL  144  524   90  36  108.0   1.0  ...   
109797  zimmery01    2018    WAS   NL   85  288   33  13   51.0   1.0  ...   
111393  zimmery01    2019    WAS   NL   52  171   20   6   27.0   0.0  ...   
114511  zimmery01    2021    WAS   NL  110  255   27  14   46.0   0.0  ...   

               K%        BB%         SB%  DebutAge       full_name  allstar  \
90820   19.354839   4.838710         NaN      21.0  Ryan Zimmerman      NaN   
92237   17.416546   9.869376   57.894737      21.0  Ryan Zimmerman      NaN   
93676   17.241379   8.827586   80.000000      21.0  Ryan Zimmerman      NaN   
95094   15.203426   6.852248   50.000000      21.0  Ryan Zimmerman      NaN   
96512   16.951567  11.538462  100.000000      21.0  Ryan Zimmerman      1.0   
96513   16.951567  11.538462  100.000000      21.0  Ryan Zimmerman      1.0   
97904   16.091954  12.315271   80.000000      21.0  Ryan Zimmerman      NaN   
99332   16.441441  10.135135   75.000000      21.0  Ryan Zimmerman      NaN   
100777  17.873652  10.015408   71.428571      21.0  Ryan Zimmerman      NaN   
102210  20.944882   9.763780  100.000000      21.0  Ryan Zimmerman      NaN   
103666  15.416667   9.166667         NaN      21.0  Ryan Zimmerman      NaN   
105176  20.256410   8.461538  100.000000      21.0  Ryan Zimmerman      NaN   
106712  22.222222   6.410256   80.000000      21.0  Ryan Zimmerman      NaN   
108233  21.837088   7.798960  100.000000      21.0  Ryan Zimmerman      1.0   
109797  16.975309   9.567901   50.000000      21.0  Ryan Zimmerman      NaN   
111393  20.526316   8.947368         NaN      21.0  Ryan Zimmerman      NaN   
114511  28.205128   5.860806         NaN      21.0  Ryan Zimmerman      NaN   

        allstar_starter  won_award award_votes      salary  
90820               NaN        NaN         NaN         NaN  
92237               NaN        NaN         1.0    327000.0  
93676               NaN        NaN         NaN         NaN  
95094               NaN        NaN         NaN    465000.0  
96512               0.0        1.0         1.0   3325000.0  
96513               0.0        1.0         1.0   3325000.0  
97904               NaN        1.0         1.0   6350000.0  
99332               NaN        1.0         NaN   9025000.0  
100777              NaN        NaN         1.0  12000000.0  
102210              NaN        NaN         NaN  14100000.0  
103666              NaN        NaN         NaN  14000000.0  
105176              NaN        NaN         NaN  14000000.0  
106712              NaN        NaN         NaN  14000000.0  
108233              1.0        1.0         NaN         NaN  
109797              NaN        NaN         NaN         NaN  
111393              NaN        NaN         NaN         NaN  
114511              NaN        NaN         NaN         NaN  

[17 rows x 24 columns]

In [116]:
df_merged = df_merged.merge(teams_df_clean, how='left', on=['teamID', 'yearID'])

In [117]:
df_merged[df_merged['playerID'] == 'zimmery01']

playerID  yearID teamID lgID_x    G   AB    R  HR    RBI    SB  ...  \
90820   zimmery01    2005    WAS     NL   20   58    6   0    6.0   0.0  ...   
92237   zimmery01    2006    WAS     NL  157  614   84  20  110.0  11.0  ...   
93676   zimmery01    2007    WAS     NL  162  653   99  24   91.0   4.0  ...   
95094   zimmery01    2008    WAS     NL  106  428   51  14   51.0   1.0  ...   
96512   zimmery01    2009    WAS     NL  157  610  110  33  106.0   2.0  ...   
96513   zimmery01    2009    WAS     NL  157  610  110  33  106.0   2.0  ...   
97904   zimmery01    2010    WAS     NL  142  525   85  25   85.0   4.0  ...   
99332   zimmery01    2011    WAS     NL  101  395   52  12   49.0   3.0  ...   
100777  zimmery01    2012    WAS     NL  145  578   93  25   95.0   5.0  ...   
102210  zimmery01    2013    WAS     NL  147  568   84  26   79.0   6.0  ...   
103666  zimmery01    2014    WAS     NL   61  214   26   5   38.0   0.0  ...   
105176  zimmery01    2015    WAS     NL   95  346   43  16   73.0   1.0  ...   
106712  zimmery01    2016    WAS     NL  115  427   60  15   46.0   4.0  ...   
108233  zimmery01    2017    WAS     NL  144  524   90  36  108.0   1.0  ...   
109797  zimmery01    2018    WAS     NL   85  288   33  13   51.0   1.0  ...   
111393  zimmery01    2019    WAS     NL   52  171   20   6   27.0   0.0  ...   
114511  zimmery01    2021    WAS     NL  110  255   27  14   46.0   0.0  ...   

        allstar  allstar_starter  won_award  award_votes      salary  lgID_y  \
90820       NaN              NaN        NaN          NaN         NaN      NL   
92237       NaN              NaN        NaN          1.0    327000.0      NL   
93676       NaN              NaN        NaN          NaN         NaN      NL   
95094       NaN              NaN        NaN          NaN    465000.0      NL   
96512       1.0              0.0        1.0          1.0   3325000.0      NL   
96513       1.0              0.0        1.0          1.0   3325000.0      NL   
97904       NaN              NaN        1.0          1.0   6350000.0      NL   
99332       NaN              NaN        1.0          NaN   9025000.0      NL   
100777      NaN              NaN        NaN          1.0  12000000.0      NL   
102210      NaN              NaN        NaN          NaN  14100000.0      NL   
103666      NaN              NaN        NaN          NaN  14000000.0      NL   
105176      NaN              NaN        NaN          NaN  14000000.0      NL   
106712      NaN              NaN        NaN          NaN  14000000.0      NL   
108233      1.0              1.0        1.0          NaN         NaN      NL   
109797      NaN              NaN        NaN          NaN         NaN      NL   
111393      NaN              NaN        NaN          NaN         NaN      NL   
114511      NaN              NaN        NaN          NaN         NaN      NL   

        DivWin  WCWin LgWin  WSWin  
90820        N      N     N      N  
92237        N      N     N      N  
93676        N      N     N      N  
95094        N      N     N      N  
96512        N      N     N      N  
96513        N      N     N      N  
97904        N      N     N      N  
99332        N      N     N      N  
100777       Y      N     N      N  
102210       N      N     N      N  
103666       Y      N     N      N  
105176       N      N     N      N  
106712       Y      N     N      N  
108233       Y      N     N      N  
109797       N      N     N      N  
111393       N      Y     Y      Y  
114511       N      N     N      N  

[17 rows x 29 columns]

In [118]:
df_merged.drop(['lgID_x' , 'lgID_y'], axis=1, inplace=True)

In [119]:
df_merged

playerID  yearID teamID    G   AB   R  HR   RBI   SB       AVG  ...  \
0       abercda01    1871    TRO    1    4   0   0   0.0  0.0  0.000000  ...   
1        addybo01    1871    RC1   25  118  30   0  13.0  8.0  0.271186  ...   
2       allisar01    1871    CL1   29  137  28   0  19.0  3.0  0.291971  ...   
3       allisdo01    1871    WS3   27  133  28   2  27.0  1.0  0.330827  ...   
4       ansonca01    1871    RC1   25  120  29   0  16.0  6.0  0.325000  ...   
...           ...     ...    ...  ...  ...  ..  ..   ...  ...       ...  ...   
114509  zimmejo02    2021    MIL    2    1   0   0   0.0  0.0  0.000000  ...   
114510  zimmeky01    2021    KCA   52    0   0   0   0.0  0.0       NaN  ...   
114511  zimmery01    2021    WAS  110  255  27  14  46.0  0.0  0.243137  ...   
114512  zuberty01    2021    KCA   31    1   0   0   0.0  0.0  0.000000  ...   
114513  zuninmi01    2021    TBA  109  333  64  33  62.0  0.0  0.216216  ...   

                full_name  allstar  allstar_starter  won_award  award_votes  \
0       Frank Abercrombie      NaN              NaN        NaN          NaN   
1                Bob Addy      NaN              NaN        NaN          NaN   
2             Art Allison      NaN              NaN        NaN          NaN   
3            Doug Allison      NaN              NaN        NaN          NaN   
4               Cap Anson      NaN              NaN        NaN          NaN   
...                   ...      ...              ...        ...          ...   
114509  Jordan Zimmermann      NaN              NaN        NaN          NaN   
114510        Kyle Zimmer      NaN              NaN        NaN          NaN   
114511     Ryan Zimmerman      NaN              NaN        NaN          NaN   
114512        Tyler Zuber      NaN              NaN        NaN          NaN   
114513        Mike Zunino      1.0              0.0        NaN          NaN   

        salary  DivWin WCWin  LgWin  WSWin  
0          NaN     NaN   NaN      N    NaN  
1          NaN     NaN   NaN      N    NaN  
2          NaN     NaN   NaN      N    NaN  
3          NaN     NaN   NaN      N    NaN  
4          NaN     NaN   NaN      N    NaN  
...        ...     ...   ...    ...    ...  
114509     NaN       Y     N      N      N  
114510     NaN       N     N      N      N  
114511     NaN       N     N      N      N  
114512     NaN       N     N      N      N  
114513     NaN       Y     N      N      N  

[114514 rows x 27 columns]

In [120]:
df_merged['DivWin'] = df_merged['DivWin'].map({'Y' : 1 , 'N' : 0})

In [121]:
df_merged['WCWin'] = df_merged['WCWin'].map({'Y' : 1 , 'N' : 0})

In [122]:
df_merged['LgWin'] = df_merged['LgWin'].map({'Y' : 1 , 'N' : 0})

In [123]:
df_merged['WSWin'] = df_merged['WSWin'].map({'Y' : 1 , 'N' : 0})

In [124]:
df_merged

playerID  yearID teamID    G   AB   R  HR   RBI   SB       AVG  ...  \
0       abercda01    1871    TRO    1    4   0   0   0.0  0.0  0.000000  ...   
1        addybo01    1871    RC1   25  118  30   0  13.0  8.0  0.271186  ...   
2       allisar01    1871    CL1   29  137  28   0  19.0  3.0  0.291971  ...   
3       allisdo01    1871    WS3   27  133  28   2  27.0  1.0  0.330827  ...   
4       ansonca01    1871    RC1   25  120  29   0  16.0  6.0  0.325000  ...   
...           ...     ...    ...  ...  ...  ..  ..   ...  ...       ...  ...   
114509  zimmejo02    2021    MIL    2    1   0   0   0.0  0.0  0.000000  ...   
114510  zimmeky01    2021    KCA   52    0   0   0   0.0  0.0       NaN  ...   
114511  zimmery01    2021    WAS  110  255  27  14  46.0  0.0  0.243137  ...   
114512  zuberty01    2021    KCA   31    1   0   0   0.0  0.0  0.000000  ...   
114513  zuninmi01    2021    TBA  109  333  64  33  62.0  0.0  0.216216  ...   

                full_name  allstar  allstar_starter  won_award  award_votes  \
0       Frank Abercrombie      NaN              NaN        NaN          NaN   
1                Bob Addy      NaN              NaN        NaN          NaN   
2             Art Allison      NaN              NaN        NaN          NaN   
3            Doug Allison      NaN              NaN        NaN          NaN   
4               Cap Anson      NaN              NaN        NaN          NaN   
...                   ...      ...              ...        ...          ...   
114509  Jordan Zimmermann      NaN              NaN        NaN          NaN   
114510        Kyle Zimmer      NaN              NaN        NaN          NaN   
114511     Ryan Zimmerman      NaN              NaN        NaN          NaN   
114512        Tyler Zuber      NaN              NaN        NaN          NaN   
114513        Mike Zunino      1.0              0.0        NaN          NaN   

        salary  DivWin WCWin  LgWin  WSWin  
0          NaN     NaN   NaN    0.0    NaN  
1          NaN     NaN   NaN    0.0    NaN  
2          NaN     NaN   NaN    0.0    NaN  
3          NaN     NaN   NaN    0.0    NaN  
4          NaN     NaN   NaN    0.0    NaN  
...        ...     ...   ...    ...    ...  
114509     NaN     1.0   0.0    0.0    0.0  
114510     NaN     0.0   0.0    0.0    0.0  
114511     NaN     0.0   0.0    0.0    0.0  
114512     NaN     0.0   0.0    0.0    0.0  
114513     NaN     1.0   0.0    0.0    0.0  

[114514 rows x 27 columns]

In [125]:
salary2_df_clean

full_name       salary2  yearID
0        Albert Belle  $12,868,670     2000
1     Bernie Williams  $12,357,143     2000
2        Larry Walker  $12,142,857     2000
3         Mike Piazza  $12,071,429     2000
4           Mo Vaughn  $11,166,667     2000
...               ...           ...     ...
9285   Chas McCormick     $570,500     2021
9286       Jose Rojas     $570,500     2021
9287        Ka'ai Tom     $570,500     2021
9288  Taylor Trammell     $570,500     2021
9289    Andrew Vaughn     $570,500     2021

[9290 rows x 3 columns]

In [126]:
df_merged = df_merged.merge(salary2_df_clean, how='left', on=['full_name', 'yearID'])

In [127]:
df_merged

playerID  yearID teamID    G   AB   R  HR   RBI   SB       AVG  ...  \
0       abercda01    1871    TRO    1    4   0   0   0.0  0.0  0.000000  ...   
1        addybo01    1871    RC1   25  118  30   0  13.0  8.0  0.271186  ...   
2       allisar01    1871    CL1   29  137  28   0  19.0  3.0  0.291971  ...   
3       allisdo01    1871    WS3   27  133  28   2  27.0  1.0  0.330827  ...   
4       ansonca01    1871    RC1   25  120  29   0  16.0  6.0  0.325000  ...   
...           ...     ...    ...  ...  ...  ..  ..   ...  ...       ...  ...   
114549  zimmejo02    2021    MIL    2    1   0   0   0.0  0.0  0.000000  ...   
114550  zimmeky01    2021    KCA   52    0   0   0   0.0  0.0       NaN  ...   
114551  zimmery01    2021    WAS  110  255  27  14  46.0  0.0  0.243137  ...   
114552  zuberty01    2021    KCA   31    1   0   0   0.0  0.0  0.000000  ...   
114553  zuninmi01    2021    TBA  109  333  64  33  62.0  0.0  0.216216  ...   

        allstar  allstar_starter  won_award  award_votes  salary  DivWin  \
0           NaN              NaN        NaN          NaN     NaN     NaN   
1           NaN              NaN        NaN          NaN     NaN     NaN   
2           NaN              NaN        NaN          NaN     NaN     NaN   
3           NaN              NaN        NaN          NaN     NaN     NaN   
4           NaN              NaN        NaN          NaN     NaN     NaN   
...         ...              ...        ...          ...     ...     ...   
114549      NaN              NaN        NaN          NaN     NaN     1.0   
114550      NaN              NaN        NaN          NaN     NaN     0.0   
114551      NaN              NaN        NaN          NaN     NaN     0.0   
114552      NaN              NaN        NaN          NaN     NaN     0.0   
114553      1.0              0.0        NaN          NaN     NaN     1.0   

        WCWin LgWin  WSWin      salary2  
0         NaN   0.0    NaN          NaN  
1         NaN   0.0    NaN          NaN  
2         NaN   0.0    NaN          NaN  
3         NaN   0.0    NaN          NaN  
4         NaN   0.0    NaN          NaN  
...       ...   ...    ...          ...  
114549    0.0   0.0    0.0          NaN  
114550    0.0   0.0    0.0          NaN  
114551    0.0   0.0    0.0  $1,000,000   
114552    0.0   0.0    0.0          NaN  
114553    0.0   0.0    0.0  $2,000,000   

[114554 rows x 28 columns]

In [128]:
df_merged = df_merged.merge(salary3_df_clean, how='left', on=['full_name', 'yearID'])

In [129]:
df_merged

playerID  yearID teamID    G   AB   R  HR   RBI   SB       AVG  ...  \
0       abercda01    1871    TRO    1    4   0   0   0.0  0.0  0.000000  ...   
1        addybo01    1871    RC1   25  118  30   0  13.0  8.0  0.271186  ...   
2       allisar01    1871    CL1   29  137  28   0  19.0  3.0  0.291971  ...   
3       allisdo01    1871    WS3   27  133  28   2  27.0  1.0  0.330827  ...   
4       ansonca01    1871    RC1   25  120  29   0  16.0  6.0  0.325000  ...   
...           ...     ...    ...  ...  ...  ..  ..   ...  ...       ...  ...   
114919  zimmejo02    2021    MIL    2    1   0   0   0.0  0.0  0.000000  ...   
114920  zimmeky01    2021    KCA   52    0   0   0   0.0  0.0       NaN  ...   
114921  zimmery01    2021    WAS  110  255  27  14  46.0  0.0  0.243137  ...   
114922  zuberty01    2021    KCA   31    1   0   0   0.0  0.0  0.000000  ...   
114923  zuninmi01    2021    TBA  109  333  64  33  62.0  0.0  0.216216  ...   

        allstar_starter  won_award  award_votes  salary_x  DivWin  WCWin  \
0                   NaN        NaN          NaN       NaN     NaN    NaN   
1                   NaN        NaN          NaN       NaN     NaN    NaN   
2                   NaN        NaN          NaN       NaN     NaN    NaN   
3                   NaN        NaN          NaN       NaN     NaN    NaN   
4                   NaN        NaN          NaN       NaN     NaN    NaN   
...                 ...        ...          ...       ...     ...    ...   
114919              NaN        NaN          NaN       NaN     1.0    0.0   
114920              NaN        NaN          NaN       NaN     0.0    0.0   
114921              NaN        NaN          NaN       NaN     0.0    0.0   
114922              NaN        NaN          NaN       NaN     0.0    0.0   
114923              0.0        NaN          NaN       NaN     1.0    0.0   

        LgWin WSWin      salary2   salary_y  
0         0.0   NaN          NaN        NaN  
1         0.0   NaN          NaN        NaN  
2         0.0   NaN          NaN        NaN  
3         0.0   NaN          NaN        NaN  
4         0.0   NaN          NaN        NaN  
...       ...   ...          ...        ...  
114919    0.0   0.0          NaN   570500.0  
114920    0.0   0.0          NaN   588700.0  
114921    0.0   0.0  $1,000,000   1000000.0  
114922    0.0   0.0          NaN   570500.0  
114923    0.0   0.0  $2,000,000   2000000.0  

[114924 rows x 29 columns]

In [130]:
df_merged_clean = df_merged[(df_merged['yearID']>= 1984) & (df_merged['yearID']<= 2021)]

In [131]:
df_merged_clean

playerID  yearID teamID    G   AB   R  HR   RBI   SB       AVG  ...  \
63543    aasedo01    1984    CAL   23    0   0   0   0.0  0.0       NaN  ...   
63544   abbotgl01    1984    DET   13    0   0   0   0.0  0.0       NaN  ...   
63545   ackerji01    1984    TOR   32    0   0   0   0.0  0.0       NaN  ...   
63546   agostju01    1984    CHA   49    0   0   0   0.0  0.0       NaN  ...   
63547   aguaylu01    1984    PHI   58   72  15   3  11.0  0.0  0.277778  ...   
...           ...     ...    ...  ...  ...  ..  ..   ...  ...       ...  ...   
114919  zimmejo02    2021    MIL    2    1   0   0   0.0  0.0  0.000000  ...   
114920  zimmeky01    2021    KCA   52    0   0   0   0.0  0.0       NaN  ...   
114921  zimmery01    2021    WAS  110  255  27  14  46.0  0.0  0.243137  ...   
114922  zuberty01    2021    KCA   31    1   0   0   0.0  0.0  0.000000  ...   
114923  zuninmi01    2021    TBA  109  333  64  33  62.0  0.0  0.216216  ...   

        allstar_starter  won_award  award_votes  salary_x  DivWin  WCWin  \
63543               NaN        NaN          NaN       NaN     0.0    NaN   
63544               NaN        NaN          NaN       NaN     1.0    NaN   
63545               NaN        NaN          NaN       NaN     0.0    NaN   
63546               NaN        NaN          NaN       NaN     0.0    NaN   
63547               NaN        NaN          NaN       NaN     0.0    NaN   
...                 ...        ...          ...       ...     ...    ...   
114919              NaN        NaN          NaN       NaN     1.0    0.0   
114920              NaN        NaN          NaN       NaN     0.0    0.0   
114921              NaN        NaN          NaN       NaN     0.0    0.0   
114922              NaN        NaN          NaN       NaN     0.0    0.0   
114923              0.0        NaN          NaN       NaN     1.0    0.0   

        LgWin WSWin      salary2   salary_y  
63543     0.0   0.0          NaN        NaN  
63544     1.0   1.0          NaN        NaN  
63545     0.0   0.0          NaN        NaN  
63546     0.0   0.0          NaN        NaN  
63547     0.0   0.0          NaN        NaN  
...       ...   ...          ...        ...  
114919    0.0   0.0          NaN   570500.0  
114920    0.0   0.0          NaN   588700.0  
114921    0.0   0.0  $1,000,000   1000000.0  
114922    0.0   0.0          NaN   570500.0  
114923    0.0   0.0  $2,000,000   2000000.0  

[51381 rows x 29 columns]

In [132]:
df_merged_clean.columns

Index(['playerID', 'yearID', 'teamID', 'G', 'AB', 'R', 'HR', 'RBI', 'SB',
       'AVG', 'OBP', 'SLG', 'OPS', 'K%', 'BB%', 'SB%', 'DebutAge', 'full_name',
       'allstar', 'allstar_starter', 'won_award', 'award_votes', 'salary_x',
       'DivWin', 'WCWin', 'LgWin', 'WSWin', 'salary2', 'salary_y'],
      dtype='object')

In [133]:
df_merged_clean = (df_merged_clean[df_merged_clean['AB'] >= 125])

In [134]:
df_merged_clean = df_merged_clean.drop_duplicates()

In [135]:
df_merged_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14742 entries, 63548 to 114923
Data columns (total 29 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   playerID         14742 non-null  object 
 1   yearID           14742 non-null  int64  
 2   teamID           14742 non-null  object 
 3   G                14742 non-null  int64  
 4   AB               14742 non-null  int64  
 5   R                14742 non-null  int64  
 6   HR               14742 non-null  int64  
 7   RBI              14742 non-null  float64
 8   SB               14742 non-null  float64
 9   AVG              14742 non-null  float64
 10  OBP              14742 non-null  float64
 11  SLG              14742 non-null  float64
 12  OPS              14742 non-null  float64
 13  K%               14742 non-null  float64
 14  BB%              14742 non-null  float64
 15  SB%              13221 non-null  float64
 16  DebutAge         14742 non-null  float64
 17  full_na

In [136]:
df_merged_clean['salary2'] = df_merged_clean['salary2'].str.replace('$', '').str.replace(',', '').astype('float')


In [137]:
df_merged_clean

playerID  yearID teamID    G   AB    R  HR    RBI    SB       AVG  \
63548   aikenwi01    1984    TOR   93  234   21  11   26.0   0.0  0.205128   
63553   almonbi01    1984    OAK  106  211   24   7   16.0   5.0  0.222749   
63556   anderda02    1984    LAN  121  374   51   3   34.0  15.0  0.251337   
63561   armasto01    1984    BOS  157  639  107  43  123.0   1.0  0.267606   
63564   ashbyal01    1984    HOU   66  191   16   4   27.0   0.0  0.261780   
...           ...     ...    ...  ...  ...  ...  ..    ...   ...       ...   
114907  yastrmi01    2021    SFN  139  468   75  25   71.0   4.0  0.224359   
114908  yelicch01    2021    MIL  117  399   70   9   51.0   9.0  0.248120   
114917  zimmebr01    2021    CLE   99  299   44   8   35.0  15.0  0.227425   
114921  zimmery01    2021    WAS  110  255   27  14   46.0   0.0  0.243137   
114923  zuninmi01    2021    TBA  109  333   64  33   62.0   0.0  0.216216   

        ...  allstar_starter  won_award  award_votes  salary_x  DivWin  WCWin  \
63548   ...              NaN        NaN          NaN       NaN     0.0    NaN   
63553   ...              NaN        NaN          NaN       NaN     0.0    NaN   
63556   ...              NaN        NaN          NaN       NaN     0.0    NaN   
63561   ...              0.0        1.0          1.0       NaN     0.0    NaN   
63564   ...              NaN        NaN          NaN       NaN     0.0    NaN   
...     ...              ...        ...          ...       ...     ...    ...   
114907  ...              NaN        NaN          NaN       NaN     1.0    0.0   
114908  ...              NaN        NaN          NaN       NaN     1.0    0.0   
114917  ...              NaN        NaN          NaN       NaN     0.0    0.0   
114921  ...              NaN        NaN          NaN       NaN     0.0    0.0   
114923  ...              0.0        NaN          NaN       NaN     1.0    0.0   

        LgWin WSWin     salary2    salary_y  
63548     0.0   0.0         NaN         NaN  
63553     0.0   0.0         NaN         NaN  
63556     0.0   0.0         NaN         NaN  
63561     0.0   0.0         NaN         NaN  
63564     0.0   0.0         NaN         NaN  
...       ...   ...         ...         ...  
114907    0.0   0.0    600000.0         NaN  
114908    0.0   0.0  14000000.0  14000000.0  
114917    0.0   0.0         NaN    570500.0  
114921    0.0   0.0   1000000.0   1000000.0  
114923    0.0   0.0   2000000.0   2000000.0  

[14742 rows x 29 columns]

In [139]:
df_merged_clean['salary'] = df_merged_clean['salary_x'].fillna(df_merged_clean['salary2'])

In [140]:
df_merged_clean.tail(30)

playerID  yearID teamID    G   AB   R  HR   RBI    SB       AVG  ...  \
114785  uriasra01    2021    BAL   85  262  33   7  38.0   1.0  0.278626  ...   
114787  urshegi01    2021    NYA  116  420  42  14  49.0   1.0  0.266667  ...   
114788  valaipa01    2021    BAL   91  259  17   5  25.0   1.0  0.200772  ...   
114793  vanmejo01    2021    ARI  112  274  26   6  36.0   3.0  0.211679  ...   
114797  varshda01    2021    ARI   95  284  41  11  38.0   6.0  0.246479  ...   
114799  vaughan01    2021    CHA  127  417  56  15  48.0   1.0  0.235012  ...   
114800  vazquch01    2021    BOS  138  458  51   6  49.0   8.0  0.257642  ...   
114804  verdual01    2021    BOS  146  544  88  13  63.0   6.0  0.288603  ...   
114809  villajo01    2021    NYN  142  454  63  18  42.0  14.0  0.248899  ...   
114811  vogelda01    2021    MIL   93  215  30   9  24.0   0.0  0.218605  ...   
114812   vogtst01    2021    ARI   52  132  17   5  17.0   0.0  0.212121  ...   
114814   voitlu01    2021    NYA   68  213  26  11  35.0   0.0  0.239437  ...   
114817  vottojo01    2021    CIN  129  448  73  36  99.0   1.0  0.265625  ...   
114823   wadela01    2021    SFN  109  336  52  18  56.0   6.0  0.252976  ...   
114824   wadety01    2021    NYA  103  127  31   0   5.0  17.0  0.267717  ...   
114826  walkech02    2021    ARI  115  401  55  10  46.0   0.0  0.244389  ...   
114829  wallsta01    2021    TBA   54  152  15   1  15.0   4.0  0.210526  ...   
114830  walshja01    2021    LAA  144  530  70  29  98.0   2.0  0.277358  ...   
114833   wardta01    2021    LAA   65  208  33   8  33.0   1.0  0.250000  ...   
114855  wendljo01    2021    TBA  136  460  73  11  54.0   8.0  0.265217  ...   
114857  whiteel04    2021    TEX   64  198  26   6  15.0   4.0  0.176768  ...   
114882  winkeje01    2021    CIN  110  423  77  24  71.0   1.0  0.304965  ...   
114884  wisdopa01    2021    CHN  106  338  54  28  61.0   4.0  0.230769  ...   
114892   wongko01    2021    MIL  116  445  70  14  50.0  12.0  0.271910  ...   
114901  wynnsau01    2021    BAL   45  130  14   4  14.0   1.0  0.184615  ...   
114907  yastrmi01    2021    SFN  139  468  75  25  71.0   4.0  0.224359  ...   
114908  yelicch01    2021    MIL  117  399  70   9  51.0   9.0  0.248120  ...   
114917  zimmebr01    2021    CLE   99  299  44   8  35.0  15.0  0.227425  ...   
114921  zimmery01    2021    WAS  110  255  27  14  46.0   0.0  0.243137  ...   
114923  zuninmi01    2021    TBA  109  333  64  33  62.0   0.0  0.216216  ...   

        won_award  award_votes  salary_x  DivWin  WCWin  LgWin  WSWin  \
114785        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114787        NaN          NaN       NaN     0.0    1.0    0.0    0.0   
114788        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114793        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114797        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114799        NaN          NaN       NaN     1.0    0.0    0.0    0.0   
114800        NaN          NaN       NaN     0.0    1.0    0.0    0.0   
114804        NaN          NaN       NaN     0.0    1.0    0.0    0.0   
114809        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114811        NaN          NaN       NaN     1.0    0.0    0.0    0.0   
114812        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114814        NaN          NaN       NaN     0.0    1.0    0.0    0.0   
114817        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114823        NaN          NaN       NaN     1.0    0.0    0.0    0.0   
114824        NaN          NaN       NaN     0.0    1.0    0.0    0.0   
114826        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114829        NaN          NaN       NaN     1.0    0.0    0.0    0.0   
114830        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114833        NaN          NaN       NaN     0.0    0.0    0.0    0.0   
114855        NaN          NaN       

In [142]:
df_merged_clean['salary'] = df_merged_clean['salary_x'].fillna(df_merged_clean['salary_y'])

In [143]:
df_merged_clean.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 14742 entries, 63548 to 114923
Data columns (total 30 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   playerID         14742 non-null  object 
 1   yearID           14742 non-null  int64  
 2   teamID           14742 non-null  object 
 3   G                14742 non-null  int64  
 4   AB               14742 non-null  int64  
 5   R                14742 non-null  int64  
 6   HR               14742 non-null  int64  
 7   RBI              14742 non-null  float64
 8   SB               14742 non-null  float64
 9   AVG              14742 non-null  float64
 10  OBP              14742 non-null  float64
 11  SLG              14742 non-null  float64
 12  OPS              14742 non-null  float64
 13  K%               14742 non-null  float64
 14  BB%              14742 non-null  float64
 15  SB%              13221 non-null  float64
 16  DebutAge         14742 non-null  float64
 17  full_na

In [145]:
df_merged_clean.drop(['salary_x', 'salary_y' , 'salary2', 'teamID'], axis=1, inplace=True)

In [146]:
column2 = df_merged_clean.pop('full_name')

In [147]:
df_merged_clean.insert(1, 'full_name', column2)

In [148]:
column3 = df_merged_clean.pop('salary')

In [149]:
df_merged_clean.insert(2, 'salary', column3)

In [150]:
column4 = df_merged_clean.pop('DebutAge')

In [151]:
df_merged_clean.insert(3, 'DebutAge', column4)

In [152]:
df_merged_clean

playerID         full_name      salary  DebutAge  yearID    G   AB  \
63548   aikenwi01     Willie Aikens         NaN      23.0    1984   93  234   
63553   almonbi01        Bill Almon         NaN      22.0    1984  106  211   
63556   anderda02     Dave Anderson         NaN      23.0    1984  121  374   
63561   armasto01        Tony Armas         NaN      23.0    1984  157  639   
63564   ashbyal01        Alan Ashby         NaN      22.0    1984   66  191   
...           ...               ...         ...       ...     ...  ...  ...   
114907  yastrmi01  Mike Yastrzemski         NaN      29.0    2021  139  468   
114908  yelicch01  Christian Yelich  14000000.0      22.0    2021  117  399   
114917  zimmebr01    Bradley Zimmer    570500.0      25.0    2021   99  299   
114921  zimmery01    Ryan Zimmerman   1000000.0      21.0    2021  110  255   
114923  zuninmi01       Mike Zunino   2000000.0      22.0    2021  109  333   

          R  HR    RBI  ...        BB%         SB%  allstar  allstar_starter  \
63548    21  11   26.0  ...  11.278195         NaN      NaN              NaN   
63553    24   7   16.0  ...   4.444444   41.666667      NaN              NaN   
63556    51   3   34.0  ...  11.212815   75.000000      NaN              NaN   
63561   107  43  123.0  ...   5.959302   25.000000      1.0              0.0   
63564    16   4   27.0  ...   9.954751         NaN      NaN              NaN   
...     ...  ..    ...  ...        ...         ...      ...              ...   
114907   75  25   71.0  ...  10.261194  100.000000      NaN              NaN   
114908   70   9   51.0  ...  15.625000   75.000000      NaN              NaN   
114917   44   8   35.0  ...   8.620690   83.333333      NaN              NaN   
114921   27  14   46.0  ...   5.860806         NaN      NaN              NaN   
114923   64  33   62.0  ...   9.066667         NaN      1.0              0.0   

        won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
63548         NaN          NaN     0.0    NaN    0.0    0.0  
63553         NaN          NaN     0.0    NaN    0.0    0.0  
63556         NaN          NaN     0.0    NaN    0.0    0.0  
63561         1.0          1.0     0.0    NaN    0.0    0.0  
63564         NaN          NaN     0.0    NaN    0.0    0.0  
...           ...          ...     ...    ...    ...    ...  
114907        NaN          NaN     1.0    0.0    0.0    0.0  
114908        NaN          NaN     1.0    0.0    0.0    0.0  
114917        NaN          NaN     0.0    0.0    0.0    0.0  
114921        NaN          NaN     0.0    0.0    0.0    0.0  
114923        NaN          NaN     1.0    0.0    0.0    0.0  

[14742 rows x 26 columns]

In [153]:
df_merged_clean.isna().sum()

playerID               0
full_name              0
salary               501
DebutAge               0
yearID                 0
G                      0
AB                     0
R                      0
HR                     0
RBI                    0
SB                     0
AVG                    0
OBP                    0
SLG                    0
OPS                    0
K%                     0
BB%                    0
SB%                 1521
allstar            13130
allstar_starter    13130
won_award          13392
award_votes        13111
DivWin               325
WCWin               3859
LgWin                325
WSWin                325
dtype: int64

In [154]:
df_merged_clean['allstar'] = df_merged_clean['allstar'].fillna(0)

In [155]:
df_merged_clean.isna().sum()

playerID               0
full_name              0
salary               501
DebutAge               0
yearID                 0
G                      0
AB                     0
R                      0
HR                     0
RBI                    0
SB                     0
AVG                    0
OBP                    0
SLG                    0
OPS                    0
K%                     0
BB%                    0
SB%                 1521
allstar                0
allstar_starter    13130
won_award          13392
award_votes        13111
DivWin               325
WCWin               3859
LgWin                325
WSWin                325
dtype: int64

In [156]:
df_merged_clean['allstar_starter'] = df_merged_clean['allstar_starter'].fillna(0)

In [157]:
df_merged_clean['won_award'] = df_merged_clean['won_award'].fillna(0)

In [158]:
df_merged_clean['award_votes'] = df_merged_clean['award_votes'].fillna(0)

In [159]:
df_merged_clean['DivWin'] = df_merged_clean['DivWin'].fillna(0)

In [160]:
df_merged_clean['WCWin'] = df_merged_clean['WCWin'].fillna(0)

In [161]:
df_merged_clean['LgWin'] = df_merged_clean['LgWin'].fillna(0)

In [162]:
df_merged_clean['WSWin'] = df_merged_clean['WSWin'].fillna(0)

In [164]:
df_merged_clean['SB%'] = df_merged_clean['SB%'].fillna(0)

In [165]:
df_merged_clean.isna().sum()

playerID             0
full_name            0
salary             501
DebutAge             0
yearID               0
G                    0
AB                   0
R                    0
HR                   0
RBI                  0
SB                   0
AVG                  0
OBP                  0
SLG                  0
OPS                  0
K%                   0
BB%                  0
SB%                  0
allstar              0
allstar_starter      0
won_award            0
award_votes          0
DivWin               0
WCWin                0
LgWin                0
WSWin                0
dtype: int64

In [166]:
df_merged_clean.shape

(14742, 26)

In [167]:
df_merged_clean.dropna(axis=0, inplace=True)


In [168]:
df_merged_clean.shape

(14241, 26)

In [169]:
df_merged_clean.columns

Index(['playerID', 'full_name', 'salary', 'DebutAge', 'yearID', 'G', 'AB', 'R',
       'HR', 'RBI', 'SB', 'AVG', 'OBP', 'SLG', 'OPS', 'K%', 'BB%', 'SB%',
       'allstar', 'allstar_starter', 'won_award', 'award_votes', 'DivWin',
       'WCWin', 'LgWin', 'WSWin'],
      dtype='object')

In [250]:
(df_merged_clean['playerID'].value_counts()>=6).sum()

1057

In [285]:
(df_merged_clean['playerID'].value_counts()>=6)

Index(['griffke02', 'vizquom01', 'gonzaal02', 'sheffga01', 'gonzalu01',
       'beltrca01', 'bondsba01', 'rodrial01', 'gonzaal01', 'youngch04',
       ...
       'wohlfji01', 'evansph01', 'brugmja01', 'wittke01', 'rodrica01',
       'peguest01', 'garciad02', 'rogerja02', 'velasgu01', 'hernayo02'],
      dtype='object', length=2470)

In [291]:
#df_merged_clean[df_merged_clean.groupby("playerID").filter(lambda x: x['playerID'].value_counts() >= 6 )]

In [300]:
mask = (df_merged_clean['playerID'].value_counts()>=6) == True
ds = df_merged_clean['playerID'].value_counts()>=6 
ds= ds[mask]

In [301]:
list6 = list(ds.index)

In [302]:
mask2 = df_merged_clean['playerID'].isin(list6)

In [303]:
mask2

64594     False
64602     False
64603      True
64606     False
64608     False
          ...  
114901    False
114908     True
114917    False
114921     True
114923     True
Name: playerID, Length: 14241, dtype: bool

In [304]:
mask2.value_counts()

True     10771
False     3470
Name: playerID, dtype: int64

In [305]:
final_df = df_merged_clean[mask2]

In [306]:
final_df

playerID         full_name      salary  DebutAge  yearID    G   AB  \
64603   anderda02     Dave Anderson     60000.0      23.0    1985   77  221   
64611   backmwa01     Wally Backman    200000.0      21.0    1985  145  520   
64614   baineha01     Harold Baines    675000.0      21.0    1985  160  640   
64619   balbost01     Steve Balboni    205000.0      24.0    1985  160  600   
64624   barfije01    Jesse Barfield    325000.0      22.0    1985  155  539   
...           ...               ...         ...       ...     ...  ...  ...   
114817  vottojo01        Joey Votto  25000000.0      24.0    2021  129  448   
114892   wongko01       Kolten Wong   7202565.0      23.0    2021  116  445   
114908  yelicch01  Christian Yelich  14000000.0      22.0    2021  117  399   
114921  zimmery01    Ryan Zimmerman   1000000.0      21.0    2021  110  255   
114923  zuninmi01       Mike Zunino   2000000.0      22.0    2021  109  333   

         R  HR    RBI  ...        BB%         SB%  allstar  allstar_starter  \
64603   24   4   18.0  ...  14.339623   55.555556      0.0              0.0   
64611   77   1   38.0  ...   6.434783   71.428571      0.0              0.0   
64614   86  22  113.0  ...   7.132668   50.000000      1.0              0.0   
64619   74  36   88.0  ...   8.408408   50.000000      0.0              0.0   
64624   94  27   84.0  ...  11.507293   73.333333      0.0              0.0   
...     ..  ..    ...  ...        ...         ...      ...              ...   
114817  73  36   99.0  ...  15.398887  100.000000      0.0              0.0   
114892  70  14   50.0  ...   6.490872   70.588235      0.0              0.0   
114908  70   9   51.0  ...  15.625000   75.000000      0.0              0.0   
114921  27  14   46.0  ...   5.860806    0.000000      0.0              0.0   
114923  64  33   62.0  ...   9.066667    0.000000      1.0              0.0   

        won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
64603         0.0          0.0     1.0    0.0    0.0    0.0  
64611         0.0          0.0     0.0    0.0    0.0    0.0  
64614         1.0          1.0     0.0    0.0    0.0    0.0  
64619         0.0          1.0     1.0    0.0    1.0    1.0  
64624         0.0          1.0     1.0    0.0    0.0    0.0  
...           ...          ...     ...    ...    ...    ...  
114817        0.0          0.0     0.0    0.0    0.0    0.0  
114892        0.0          0.0     1.0    0.0    0.0    0.0  
114908        0.0          0.0     1.0    0.0    0.0    0.0  
114921        0.0          0.0     0.0    0.0    0.0    0.0  
114923        0.0          0.0     1.0    0.0    0.0    0.0  

[10771 rows x 26 columns]

In [308]:
final_df['playerID'].value_counts()

griffke02    25
gonzaal02    24
vizquom01    24
sheffga01    23
gonzalu01    22
             ..
davisru01     6
moutoja01     6
lynnfr01      6
canhama01     6
pearcst01     6
Name: playerID, Length: 1057, dtype: int64

In [241]:
zimm

playerID       full_name      salary  DebutAge  yearID    G   AB  \
92477   zimmery01  Ryan Zimmerman    327000.0      21.0    2006  157  614   
93928   zimmery01  Ryan Zimmerman    400000.0      21.0    2007  162  653   
95355   zimmery01  Ryan Zimmerman    465000.0      21.0    2008  106  428   
96783   zimmery01  Ryan Zimmerman   3325000.0      21.0    2009  157  610   
98199   zimmery01  Ryan Zimmerman   6350000.0      21.0    2010  142  525   
99634   zimmery01  Ryan Zimmerman   9025000.0      21.0    2011  101  395   
101088  zimmery01  Ryan Zimmerman  12000000.0      21.0    2012  145  578   
102530  zimmery01  Ryan Zimmerman  14100000.0      21.0    2013  147  568   
103997  zimmery01  Ryan Zimmerman  14000000.0      21.0    2014   61  214   
105517  zimmery01  Ryan Zimmerman  14000000.0      21.0    2015   95  346   
107068  zimmery01  Ryan Zimmerman  14000000.0      21.0    2016  115  427   
108596  zimmery01  Ryan Zimmerman  14000000.0      21.0    2017  144  524   
110165  zimmery01  Ryan Zimmerman  14000000.0      21.0    2018   85  288   

          R  HR    RBI  ...        BB%         SB%  allstar  allstar_starter  \
92477    84  20  110.0  ...   9.869376   57.894737      0.0              0.0   
93928    99  24   91.0  ...   8.827586   80.000000      0.0              0.0   
95355    51  14   51.0  ...   6.852248   50.000000      0.0              0.0   
96783   110  33  106.0  ...  11.538462  100.000000      1.0              0.0   
98199    85  25   85.0  ...  12.315271   80.000000      0.0              0.0   
99634    52  12   49.0  ...  10.135135   75.000000      0.0              0.0   
101088   93  25   95.0  ...  10.015408   71.428571      0.0              0.0   
102530   84  26   79.0  ...   9.763780  100.000000      0.0              0.0   
103997   26   5   38.0  ...   9.166667    0.000000      0.0              0.0   
105517   43  16   73.0  ...   8.461538  100.000000      0.0              0.0   
107068   60  15   46.0  ...   6.410256   80.000000      0.0              0.0   
108596   90  36  108.0  ...   7.798960  100.000000      1.0              1.0   
110165   33  13   51.0  ...   9.567901   50.000000      0.0              0.0   

        won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
92477         0.0          1.0     0.0    0.0    0.0    0.0  
93928         0.0          0.0     0.0    0.0    0.0    0.0  
95355         0.0          0.0     0.0    0.0    0.0    0.0  
96783         1.0          1.0     0.0    0.0    0.0    0.0  
98199         1.0          1.0     0.0    0.0    0.0    0.0  
99634         1.0          0.0     0.0    0.0    0.0    0.0  
101088        0.0          1.0     1.0    0.0    0.0    0.0  
102530        0.0          0.0     0.0    0.0    0.0    0.0  
103997        0.0          0.0     1.0    0.0    0.0    0.0  
105517        0.0          0.0     0.0    0.0    0.0    0.0  
107068        0.0          0.0     1.0    0.0    0.0    0.0  
108596        1.0          0.0     1.0    0.0    0.0    0.0  
110165        0.0          0.0     0.0    0.0    0.0    0.0  

[13 rows x 26 columns]

In [172]:
zimm.columns

Index(['playerID', 'full_name', 'salary', 'DebutAge', 'yearID', 'G', 'AB', 'R',
       'HR', 'RBI', 'SB', 'AVG', 'OBP', 'SLG', 'OPS', 'K%', 'BB%', 'SB%',
       'allstar', 'allstar_starter', 'won_award', 'award_votes', 'DivWin',
       'WCWin', 'LgWin', 'WSWin'],
      dtype='object')

In [173]:
cols = ['playerID', 'full_name','DebutAge', 'yearID', 'G', 'AB', 'R', 'HR', 'RBI', 'SB',
       'AVG', 'OBP', 'SLG', 'OPS', 'K%', 'BB%', 'SB%',  
       'allstar', 'allstar_starter', 'won_award', 'award_votes', 'DivWin', 'WCWin', 'LgWin', 'WSWin']

In [174]:
zimm[:6][cols]

playerID       full_name  DebutAge  yearID    G   AB    R  HR    RBI  \
92477  zimmery01  Ryan Zimmerman      21.0    2006  157  614   84  20  110.0   
93928  zimmery01  Ryan Zimmerman      21.0    2007  162  653   99  24   91.0   
95355  zimmery01  Ryan Zimmerman      21.0    2008  106  428   51  14   51.0   
96783  zimmery01  Ryan Zimmerman      21.0    2009  157  610  110  33  106.0   
98199  zimmery01  Ryan Zimmerman      21.0    2010  142  525   85  25   85.0   
99634  zimmery01  Ryan Zimmerman      21.0    2011  101  395   52  12   49.0   

         SB  ...        BB%         SB%  allstar  allstar_starter  won_award  \
92477  11.0  ...   9.869376   57.894737      0.0              0.0        0.0   
93928   4.0  ...   8.827586   80.000000      0.0              0.0        0.0   
95355   1.0  ...   6.852248   50.000000      0.0              0.0        0.0   
96783   2.0  ...  11.538462  100.000000      1.0              0.0        1.0   
98199   4.0  ...  12.315271   80.000000      0.0              0.0        1.0   
99634   3.0  ...  10.135135   75.000000      0.0              0.0        1.0   

       award_votes  DivWin  WCWin  LgWin  WSWin  
92477          1.0     0.0    0.0    0.0    0.0  
93928          0.0     0.0    0.0    0.0    0.0  
95355          0.0     0.0    0.0    0.0    0.0  
96783          1.0     0.0    0.0    0.0    0.0  
98199          1.0     0.0    0.0    0.0    0.0  
99634          0.0     0.0    0.0    0.0    0.0  

[6 rows x 25 columns]

In [216]:
zimm['salary'][:6] = zimm['salary'][6:9].mean()

<ipython-input-216-fb33b0737dbc>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  zimm['salary'][:6] = zimm['salary'][6:9].mean()
/Users/jordan/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)


In [217]:
zimm[:6]

playerID       full_name        salary  DebutAge  yearID    G   AB  \
92477  zimmery01  Ryan Zimmerman  1.336667e+07      21.0    2006  157  614   
93928  zimmery01  Ryan Zimmerman  1.336667e+07      21.0    2007  162  653   
95355  zimmery01  Ryan Zimmerman  1.336667e+07      21.0    2008  106  428   
96783  zimmery01  Ryan Zimmerman  1.336667e+07      21.0    2009  157  610   
98199  zimmery01  Ryan Zimmerman  1.336667e+07      21.0    2010  142  525   
99634  zimmery01  Ryan Zimmerman  1.336667e+07      21.0    2011  101  395   

         R  HR    RBI  ...        BB%         SB%  allstar  allstar_starter  \
92477   84  20  110.0  ...   9.869376   57.894737      0.0              0.0   
93928   99  24   91.0  ...   8.827586   80.000000      0.0              0.0   
95355   51  14   51.0  ...   6.852248   50.000000      0.0              0.0   
96783  110  33  106.0  ...  11.538462  100.000000      1.0              0.0   
98199   85  25   85.0  ...  12.315271   80.000000      0.0              0.0   
99634   52  12   49.0  ...  10.135135   75.000000      0.0              0.0   

       won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
92477        0.0          1.0     0.0    0.0    0.0    0.0  
93928        0.0          0.0     0.0    0.0    0.0    0.0  
95355        0.0          0.0     0.0    0.0    0.0    0.0  
96783        1.0          1.0     0.0    0.0    0.0    0.0  
98199        1.0          1.0     0.0    0.0    0.0    0.0  
99634        1.0          0.0     0.0    0.0    0.0    0.0  

[6 rows x 26 columns]

In [251]:
ncast = df_merged_clean[df_merged_clean['playerID'] == 'springe01'].head(10)

In [227]:
ncast

playerID        full_name      salary  DebutAge  yearID    G   AB  \
103805  springe01  George Springer    500000.0      25.0    2014   78  295   
105326  springe01  George Springer    512900.0      25.0    2015  102  388   
106874  springe01  George Springer    522400.0      25.0    2016  162  644   
108388  springe01  George Springer   3900000.0      25.0    2017  140  548   
109941  springe01  George Springer  12000000.0      25.0    2018  140  544   
111537  springe01  George Springer  12000000.0      25.0    2019  122  479   
112976  springe01  George Springer  21000000.0      25.0    2020   51  189   
114662  springe01  George Springer  23666667.0      25.0    2021   78  299   

          R  HR   RBI  ...        BB%        SB%  allstar  allstar_starter  \
103805   45  20  51.0  ...  12.320917  71.428571      0.0              0.0   
105326   59  16  41.0  ...  11.086475  80.000000      0.0              0.0   
106874  116  29  82.0  ...  12.064343  47.368421      0.0              0.0   
108388  112  34  85.0  ...  10.350318  41.666667      1.0              1.0   
109941  102  22  71.0  ...  10.389610  60.000000      1.0              0.0   
111537   96  39  96.0  ...  12.208259  75.000000      1.0              1.0   
112976   37  14  32.0  ...  10.909091  33.333333      0.0              0.0   
114662   59  22  50.0  ...  11.111111  80.000000      0.0              0.0   

        won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
103805        0.0          1.0     0.0    0.0    0.0    0.0  
105326        0.0          0.0     0.0    1.0    0.0    0.0  
106874        0.0          0.0     0.0    0.0    0.0    0.0  
108388        1.0          0.0     1.0    0.0    1.0    1.0  
109941        0.0          0.0     1.0    0.0    0.0    0.0  
111537        1.0          0.0     1.0    0.0    1.0    0.0  
112976        1.0          0.0     0.0    1.0    0.0    0.0  
114662        0.0          0.0     0.0    0.0    0.0    0.0  

[8 rows x 26 columns]

In [228]:
ncast[:6][cols]

playerID        full_name  DebutAge  yearID    G   AB    R  HR   RBI  \
103805  springe01  George Springer      25.0    2014   78  295   45  20  51.0   
105326  springe01  George Springer      25.0    2015  102  388   59  16  41.0   
106874  springe01  George Springer      25.0    2016  162  644  116  29  82.0   
108388  springe01  George Springer      25.0    2017  140  548  112  34  85.0   
109941  springe01  George Springer      25.0    2018  140  544  102  22  71.0   
111537  springe01  George Springer      25.0    2019  122  479   96  39  96.0   

          SB  ...        BB%        SB%  allstar  allstar_starter  won_award  \
103805   5.0  ...  12.320917  71.428571      0.0              0.0        0.0   
105326  16.0  ...  11.086475  80.000000      0.0              0.0        0.0   
106874   9.0  ...  12.064343  47.368421      0.0              0.0        0.0   
108388   5.0  ...  10.350318  41.666667      1.0              1.0        1.0   
109941   6.0  ...  10.389610  60.000000      1.0              0.0        0.0   
111537   6.0  ...  12.208259  75.000000      1.0              1.0        1.0   

        award_votes  DivWin  WCWin  LgWin  WSWin  
103805          1.0     0.0    0.0    0.0    0.0  
105326          0.0     0.0    1.0    0.0    0.0  
106874          0.0     0.0    0.0    0.0    0.0  
108388          0.0     1.0    0.0    1.0    1.0  
109941          0.0     1.0    0.0    0.0    0.0  
111537          0.0     1.0    0.0    1.0    0.0  

[6 rows x 25 columns]

In [266]:
ncast['salary'][:6] = ncast['salary'][6:10].mean()

/Users/jordan/opt/anaconda3/envs/learn-env/lib/python3.8/site-packages/pandas/core/indexing.py:670: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  iloc._setitem_with_indexer(indexer, value)


In [267]:
ncast_clean = ncast[:6]

In [270]:
ncast_clean

playerID        full_name      salary  DebutAge  yearID    G   AB  \
103805  springe01  George Springer  22333333.5      25.0    2014   78  295   
105326  springe01  George Springer  22333333.5      25.0    2015  102  388   
106874  springe01  George Springer  22333333.5      25.0    2016  162  644   
108388  springe01  George Springer  22333333.5      25.0    2017  140  548   
109941  springe01  George Springer  22333333.5      25.0    2018  140  544   
111537  springe01  George Springer  22333333.5      25.0    2019  122  479   

          R  HR   RBI  ...        BB%        SB%  allstar  allstar_starter  \
103805   45  20  51.0  ...  12.320917  71.428571      0.0              0.0   
105326   59  16  41.0  ...  11.086475  80.000000      0.0              0.0   
106874  116  29  82.0  ...  12.064343  47.368421      0.0              0.0   
108388  112  34  85.0  ...  10.350318  41.666667      1.0              1.0   
109941  102  22  71.0  ...  10.389610  60.000000      1.0              0.0   
111537   96  39  96.0  ...  12.208259  75.000000      1.0              1.0   

        won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
103805        0.0          1.0     0.0    0.0    0.0    0.0  
105326        0.0          0.0     0.0    1.0    0.0    0.0  
106874        0.0          0.0     0.0    0.0    0.0    0.0  
108388        1.0          0.0     1.0    0.0    1.0    1.0  
109941        0.0          0.0     1.0    0.0    0.0    0.0  
111537        1.0          0.0     1.0    0.0    1.0    0.0  

[6 rows x 26 columns]

In [271]:
#ncast.unstack()

In [272]:
#ncast_clean.melt(id_vars=['playerID', 'full_name', 'salary', 'DebutAge']).T

In [273]:
#ncast_clean.columns

In [274]:
listed = ncast_clean.stack().values

In [275]:
pd.DataFrame(listed).T

0                1            2   3     4   5    6   7   8   9    \
0  springe01  George Springer  2.23333e+07  25  2014  78  295  45  20  51   

   ...      146 147 148 149 150 151 152 153 154 155  
0  ...  12.2083  75   1   1   1   0   1   0   1   0  

[1 rows x 156 columns]

In [247]:
def getAvgSalary789(df,playerID):
    df = df[df.playerID == playerID].sort_values(by='yearID')
    if df.shape[0]<=6:
        print('Dobby never got his sock')
    else:
        #if df.shape[0]>9:
            #print('player played for more than 9 year:',df.shape[0])
            #print(df[6:9].salary.mean())
        #else:
            #print('player played for:',df.shape[0])
        print(df[6:10].salary.mean())
            
            
getAvgSalary789(df_merged_clean, 'springe01')

22333333.5


In [ ]:
[(col+'_year'+str(i)) for i in range(1,7) for col in list(df_merged_clean.columns)]

In [187]:
# cols2 = ['playerID', 'full_name', 'salary', 'DebutAge', 'yearID', 'G', 'AB', 'R',
#       'HR', 'RBI', 'SB', 'AVG', 'OBP', 'SLG', 'OPS', 'K%', 'BB%', 'SB%',
#      'allstar', 'allstar_starter', 'won_award', 'award_votes', 'DivWin',
#       'WCWin', 'LgWin', 'WSWin']

In [188]:
df_merged_clean.columns

Index(['playerID', 'full_name', 'salary', 'DebutAge', 'yearID', 'G', 'AB', 'R',
       'HR', 'RBI', 'SB', 'AVG', 'OBP', 'SLG', 'OPS', 'K%', 'BB%', 'SB%',
       'allstar', 'allstar_starter', 'won_award', 'award_votes', 'DivWin',
       'WCWin', 'LgWin', 'WSWin'],
      dtype='object')

In [189]:
pt = df_merged_clean.pivot_table(index = 'playerID')

In [190]:
pt['salary'].isna().sum()

0

In [191]:
pt

AB       AVG        BB%  DebutAge    DivWin           G  \
playerID                                                                     
abbotje01  229.500000  0.276554   6.461163      25.0  0.500000   84.500000   
abbotku01  296.666667  0.253377   6.694013      24.0  0.000000   99.833333   
abercre01  255.000000  0.211765   7.067138      26.0  0.000000  111.000000   
abernbr01  383.500000  0.255819   6.646825      24.0  0.000000   98.000000   
abnersh01  196.000000  0.261706   5.556041      21.0  0.000000   94.000000   
...               ...       ...        ...       ...       ...         ...   
zimmery01  439.733333  0.272937   9.035384      21.0  0.266667  118.600000   
zobribe01  413.071429  0.265641  12.276667      25.0  0.357143  115.714286   
zuninmi01  310.500000  0.203432   7.415022      22.0  0.125000   98.250000   
zupcibo01  339.000000  0.258384   7.423041      25.0  0.000000  132.500000   
zuvelpa01  160.000000  0.241700   6.768162      24.0  0.000000   66.000000   

                  HR         K%     LgWin       OBP  ...        SB%       SLG  \
playerID                                             ...                        
abbotje01   7.500000  13.215224  0.000000  0.316931  ...  58.333333  0.443576   
abbotku01   9.000000  25.723062  0.333333  0.299433  ...  65.357143  0.420976   
abercre01   5.000000  27.561837  0.000000  0.265018  ...  54.545455  0.333333   
abernbr01   3.500000   9.771825  0.000000  0.304067  ...  72.077922  0.346297   
abnersh01   1.000000  14.643872  0.000000  0.299399  ...  36.666667  0.330372   
...              ...        ...       ...       ...  ...        ...       ...   
zimmery01  18.933333  18.906932  0.066667  0.333862  ...  62.954887  0.467928   
zobribe01  11.857143  13.994980  0.214286  0.350422  ...  59.126195  0.423037   
zuninmi01  17.125000  33.686504  0.000000  0.276298  ...  25.000000  0.411615   
zupcibo01   2.500000  15.160114  0.000000  0.307589  ...  60.714286  0.356090   
zuvelpa01   0.000000   7.769590  0.000000  0.281796  ...  50.000000  0.294939   

              WCWin     WSWin   allstar  allstar_starter  award_votes  \
playerID                                                                
abbotje01  0.000000  0.000000  0.000000         0.000000     0.000000   
abbotku01  0.333333  0.166667  0.000000         0.000000     0.000000   
abercre01  0.000000  0.000000  0.000000         0.000000     0.000000   
abernbr01  0.000000  0.000000  0.000000         0.000000     0.000000   
abnersh01  0.000000  0.000000  0.000000         0.000000     0.000000   
...             ...       ...       ...              ...          ...   
zimmery01  0.066667  0.066667  0.133333         0.066667     0.266667   
zobribe01  0.214286  0.142857  0.214286         0.071429     0.214286   
zuninmi01  0.125000  0.000000  0.125000         0.000000     0.000000   
zupcibo01  0.000000  0.000000  0.000000         0.000000     0.000000   
zuvelpa01  0.000000  0.000000  0.000000         0.000000     0.000000   

                 salary  won_award       yearID  
playerID                                         
abbotje01  2.150000e+05   0.000000  1999.000000  
abbotku01  4.213333e+05   0.000000  1996.833333  
abercre01  3.270000e+05   0.000000  2006.000000  
abernbr01  2.075000e+05   0.000000  2001.500000  
abnersh01  2.012500e+05   0.000000  1991.000000  
...                 ...        ...          ...  
zimmery01  9.021689e+06   0.266667  2013.066667  
zobribe01  6.688479e+06   0.071429  2013.071429  
zuninmi01  1.497825e+06   0.000000  2016.625000  
zupcibo01  1.655000e+05   0.000000  1992.500000  
zuvelpa01  6.125000e+04   0.000000  1986.500000  

[2470 rows x 24 columns]

In [192]:
unique_ids = list(set(df_merged_clean['playerID']))

In [193]:
len(unique_ids)

2470

In [194]:
for player in unique_ids:
    print(df_merged_clean[df_merged_clean['playerID'] == player].head(9))

         playerID       full_name    salary  DebutAge  yearID   G   AB   R  \
102192  reckean01  Anthony Recker  490840.0      28.0    2013  50  135  17   
103631  reckean01  Anthony Recker  505340.0      28.0    2014  58  174  18   

        HR   RBI  ...       BB%   SB%  allstar  allstar_starter  won_award  \
102192   6  19.0  ...  9.210526   0.0      0.0              0.0        0.0   
103631   7  27.0  ...  5.291005  50.0      0.0              0.0        0.0   

        award_votes  DivWin  WCWin  LgWin  WSWin  
102192          0.0     0.0    0.0    0.0    0.0  
103631          0.0     0.0    0.0    0.0    0.0  

[2 rows x 26 columns]
        playerID   full_name    salary  DebutAge  yearID    G   AB   R  HR  \
64691  brockgr01  Greg Brock  150000.0      25.0    1985  129  438  64  21   
65765  brockgr01  Greg Brock  325000.0      25.0    1986  115  325  33  16   
66849  brockgr01  Greg Brock  405000.0      25.0    1987  141  532  81  13   
67955  brockgr01  Greg Brock  600000.0    

         playerID     full_name      salary  DebutAge  yearID    G   AB   R  \
101283  calhoko01  Kole Calhoun    491000.0      25.0    2013   58  195  29   
102721  calhoko01  Kole Calhoun    506000.0      25.0    2014  127  493  90   
104200  calhoko01  Kole Calhoun    537500.0      25.0    2015  159  630  78   
105722  calhoko01  Kole Calhoun   3400000.0      25.0    2016  157  594  91   
107274  calhoko01  Kole Calhoun   6000000.0      25.0    2017  155  569  77   
108815  calhoko01  Kole Calhoun   8500000.0      25.0    2018  137  491  71   
110405  calhoko01  Kole Calhoun  10833333.0      25.0    2019  152  552  92   
111973  calhoko01  Kole Calhoun   6000000.0      25.0    2020   54  190  35   
113410  calhoko01  Kole Calhoun   8000000.0      25.0    2021   51  166  17   

        HR   RBI  ...        BB%         SB%  allstar  allstar_starter  \
101283   8  32.0  ...   9.459459   50.000000      0.0              0.0   
102721  17  58.0  ...   7.076350   62.500000      0.0        

        playerID      full_name     salary  DebutAge  yearID    G   AB   R  \
73318  servasc01  Scott Servais   120000.0      24.0    1992   77  205  12   
74534  servasc01  Scott Servais   170000.0      24.0    1993   85  258  24   
75652  servasc01  Scott Servais   280000.0      24.0    1994   78  251  27   
76911  servasc01  Scott Servais   340000.0      24.0    1995   52  175  31   
78217  servasc01  Scott Servais   822500.0      24.0    1996  129  445  42   
79549  servasc01  Scott Servais  1370000.0      24.0    1997  122  385  36   
80939  servasc01  Scott Servais  1645000.0      24.0    1998  113  325  35   
82353  servasc01  Scott Servais   500000.0      24.0    1999   69  198  21   

       HR   RBI  ...        BB%         SB%  allstar  allstar_starter  \
73318   0  15.0  ...   5.676856    0.000000      0.0              0.0   
74534  11  32.0  ...   8.191126    0.000000      0.0              0.0   
75652   9  41.0  ...   3.636364    0.000000      0.0              0.0   
76911

[9 rows x 26 columns]
         playerID      full_name     salary  DebutAge  yearID    G   AB   R  \
99658   alonsyo01  Yonder Alonso  1400000.0      23.0    2012  155  549  47   
101108  alonsyo01  Yonder Alonso  1120000.0      23.0    2013   97  334  34   
102562  alonsyo01  Yonder Alonso   980000.0      23.0    2014   84  267  27   
104024  alonsyo01  Yonder Alonso  1650000.0      23.0    2015  103  354  50   
105546  alonsyo01  Yonder Alonso  2650000.0      23.0    2016  156  482  52   
107101  alonsyo01  Yonder Alonso  4000000.0      23.0    2017  100  319  52   
107102  alonsyo01  Yonder Alonso  4000000.0      23.0    2017   42  132  20   
108629  alonsyo01  Yonder Alonso  7000000.0      23.0    2018  145  516  64   
110214  alonsyo01  Yonder Alonso  8500000.0      23.0    2019   67  219  23   

        HR   RBI  ...        BB%         SB%  allstar  allstar_starter  \
99658    9  62.0  ...  11.305732  100.000000      0.0              0.0   
101108   6  45.0  ...   9.736842  100.0

        playerID       full_name    salary  DebutAge  yearID    G   AB   R  \
91072  anderbr03  Brian Anderson  330000.0      23.0    2006  134  365  46   
93949  anderbr03  Brian Anderson  395000.0      23.0    2008  109  181  24   
95377  anderbr03  Brian Anderson  440000.0      23.0    2009   65  185  25   

       HR   RBI  ...       BB%        SB%  allstar  allstar_starter  \
91072   8  33.0  ...  7.862408  36.363636      0.0              0.0   
93949   8  26.0  ...  5.181347  83.333333      0.0              0.0   
95377   2  13.0  ...  9.523810  33.333333      0.0              0.0   

       won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
91072        0.0          0.0     0.0    0.0    0.0    0.0  
93949        0.0          0.0     1.0    0.0    0.0    0.0  
95377        0.0          0.0     0.0    0.0    0.0    0.0  

[3 rows x 26 columns]
        playerID    full_name    salary  DebutAge  yearID   G   AB   R  HR  \
67319  lyonsba01  Barry Lyons   62500.0      26.0    1987

...

         playerID      full_name    salary  DebutAge  yearID    G   AB   R  \
105078  peterja01  Jace Peterson  507500.0      24.0    2015  152  528  55   
106599  peterja01  Jace Peterson  520500.0      24.0    2016  115  350  45   
108121  peterja01  Jace Peterson  555000.0      24.0    2017   89  186  15   
109682  peterja01  Jace Peterson  545000.0      24.0    2018   93  200  21   
114388  peterja01  Jace Peterson  570500.0      24.0    2021   94  259  36   

        HR   RBI  ...        BB%         SB%  allstar  allstar_starter  \
105078   6  52.0  ...   9.983361   54.545455      0.0              0.0   
106599   7  29.0  ...  13.170732   50.000000      0.0              0.0   
108121   2  17.0  ...  13.761468  100.000000      0.0              0.0   
109682   3  28.0  ...  12.765957   86.666667      0.0              0.0   
114388   6  31.0  ...  12.582781   90.909091      0.0              0.0   

        won_award  award_votes  DivWin  WCWin  LgWin  WSWin  
105078        0.0       

       playerID   full_name    salary  DebutAge  yearID    G   AB   R  HR  \
79376  orieke01  Kevin Orie  150000.0      25.0    1997  114  364  40   8   
80735  orieke01  Kevin Orie  240000.0      25.0    1998   64  204  24   2   
80736  orieke01  Kevin Orie  240000.0      25.0    1998   48  175  23   6   
82134  orieke01  Kevin Orie  240000.0      25.0    1999   77  240  26   6   

        RBI  ...        BB%    SB%  allstar  allstar_starter  won_award  \
79376  44.0  ...  10.047847   50.0      0.0              0.0        0.0   
80735  21.0  ...   7.826087   50.0      0.0              0.0        0.0   
80736  17.0  ...   8.121827  100.0      0.0              0.0        0.0   
82134  29.0  ...   8.582090  100.0      0.0              0.0        0.0   

       award_votes  DivWin  WCWin  LgWin  WSWin  
79376          1.0     0.0    0.0    0.0    0.0  
80735          0.0     0.0    1.0    0.0    0.0  
80736          0.0     0.0    0.0    0.0    0.0  
82134          0.0     0.0    0.0    0

[1 rows x 26 columns]
        playerID    full_name    salary  DebutAge  yearID   G   AB   R  HR  \
78404  wehnejo01  John Wehner  200000.0      24.0    1996  86  139  19   2   

        RBI  ...  BB%        SB%  allstar  allstar_starter  won_award  \
78404  13.0  ...  6.0  16.666667      0.0              0.0        0.0   

       award_votes  DivWin  WCWin  LgWin  WSWin  
78404          0.0     0.0    0.0    0.0    0.0  

[1 rows x 26 columns]
        playerID   full_name     salary  DebutAge  yearID    G   AB    R  HR  \
90249   hillaa01  Aaron Hill   300000.0      23.0    2005  105  361   49   3   
91615   hillaa01  Aaron Hill   336000.0      23.0    2006  155  546   70   6   
93050   hillaa01  Aaron Hill   395000.0      23.0    2007  160  608   87  17   
94504   hillaa01  Aaron Hill   410000.0      23.0    2008   55  205   19   2   
95937   hillaa01  Aaron Hill  2590000.0      23.0    2009  158  682  103  36   
97355   hillaa01  Aaron Hill  4000000.0      23.0    2010  138  528   7

         playerID      full_name    salary  DebutAge  yearID   G   AB   R  HR  \
114131  marshbr02  Brandon Marsh  570500.0      24.0    2021  70  236  27   2   

         RBI  ...       BB%        SB%  allstar  allstar_starter  won_award  \
114131  19.0  ...  7.692308  85.714286      0.0              0.0        0.0   

        award_votes  DivWin  WCWin  LgWin  WSWin  
114131          0.0     0.0    0.0    0.0    0.0  

[1 rows x 26 columns]
        playerID    full_name     salary  DebutAge  yearID    G   AB   R  HR  \
79466  reesepo01  Pokey Reese   150000.0      24.0    1997  128  397  48   4   
80848  reesepo01  Pokey Reese   220000.0      24.0    1998   59  133  20   1   
82249  reesepo01  Pokey Reese   270000.0      24.0    1999  149  585  85  10   
83683  reesepo01  Pokey Reese  1950000.0      24.0    2000  135  518  76  12   
85107  reesepo01  Pokey Reese  3200000.0      24.0    2001  133  428  50   9   
86499  reesepo01  Pokey Reese  1750000.0      24.0    2002  119  421  46 

        playerID   full_name     salary  DebutAge  yearID    G   AB   R  HR  \
87259  freelry01  Ryan Freel   300000.0      25.0    2003   43  137  23   4   
88694  freelry01  Ryan Freel   320000.0      25.0    2004  143  505  74   3   
90084  freelry01  Ryan Freel   405000.0      25.0    2005  103  369  69   4   
91460  freelry01  Ryan Freel  1300000.0      25.0    2006  132  454  67   8   
92907  freelry01  Ryan Freel  2325000.0      25.0    2007   75  277  44   3   
94351  freelry01  Ryan Freel  3000000.0      25.0    2008   48  131  17   0   

        RBI  ...        BB%        SB%  allstar  allstar_starter  won_award  \
87259  12.0  ...   6.493506  69.230769      0.0              0.0        0.0   
88694  28.0  ...  11.317568  78.723404      0.0              0.0        0.0   
90084  21.0  ...  11.832947  78.260870      0.0              0.0        0.0   
91460  27.0  ...  10.898662  77.083333      0.0              0.0        0.0   
92907  16.0  ...   5.921053  65.217391      0.0    

### Next Steps

- Better Account for 2020 Pandemic Shortened Season. 